In [1]:
from sklearn.metrics import confusion_matrix
from sklearn.metrics import roc_auc_score

import numpy as np
import pandas as pd

from torch.utils.data import TensorDataset
from torch.utils.data import DataLoader
import torch
import torch.nn as nn

import warnings
from tqdm import tqdm
import os
from pathlib import Path
# Define the device
device = "cuda" if torch.cuda.is_available() else "mps" if  torch.backends.mps.is_available() else "cpu" # torch.has_mps or
print("Using device:", device)
if (device == 'cuda'):
    print(f"Device name: {torch.cuda.get_device_name(device.index)}")
    print(f"Device memory: {torch.cuda.get_device_properties(device.index).total_memory / 1024 ** 3} GB")
elif (device == 'mps'):
    print(f"Device name: <mps>")
else:
    print("NOTE: If you have a GPU, consider using it for training.")
    print("      On a Windows machine with NVidia GPU, check this video: https://www.youtube.com/watch?v=GMSjDTU8Zlc")
    print("      On a Mac machine, run: pip3 install --pre torch torchvision torchaudio torchtext --index-url https://download.pytorch.org/whl/nightly/cpu")
device = torch.device(device)

Using device: cuda
Device name: Tesla T4
Device memory: 14.74810791015625 GB


In [2]:
from google.colab import drive
drive.mount('/content/drive')


Mounted at /content/drive


In [3]:
def run_validation(model, val_loader,loss_fn, device):
    model.eval()
    loss_sum = 0
    num_batch = len(val_loader)
    total_y_true=[]
    total_y_pred=[]
    total_y_prob=[]
    for ESP_val_df_enzy,ESP_val_df_smiles, y_val in val_loader:

        ESP_val_df_enzy = ESP_val_df_enzy.to(device)
        ESP_val_df_smiles = ESP_val_df_smiles.to(device)
        y_val = y_val.squeeze(1).to(device)

        refined_enzy_embed, refined_smiles_embed = model(ESP_val_df_enzy,ESP_val_df_smiles)
        cos_sim = torch.nn.functional.cosine_similarity(refined_enzy_embed, refined_smiles_embed, dim=1)
        loss = loss_fn(cos_sim, y_val).detach().cpu().numpy()
        loss_sum = loss_sum + loss # count all the loss in the training process
        y_pred = (cos_sim > 0.5).float().cpu().numpy() # if score > 0.5, assign label 1 otherwise 0, transfer to cpu as numpy
        total_y_true.append(y_val.cpu().numpy())
        total_y_pred.append(y_pred)
        total_y_prob.append(cos_sim.detach().cpu().numpy())

    loss_sum = loss_sum/num_batch # get the overall average loss (Notice: this method is not 100% accurate)

    arrange_y_true = np.concatenate(total_y_true, axis=0)
    arrange_y_pred = np.concatenate(total_y_pred, axis=0)
    arrange_y_prob = np.concatenate(total_y_prob, axis=0)
    tn,fp,fn,tp = confusion_matrix(arrange_y_true, arrange_y_pred).ravel()
    acc = (tp+tn)/(tp+tn+fp+fn)
    specificity = tn/(tn+fp)
    sensitivity = tp/(tp+fn)
    recall = tp/(tp+fn)
    precision = tp/(tp+fp)
    bacc = (sensitivity + specificity)/2
    MCC = (tp*tn-fp*fn)/np.sqrt((tp+fp)*(tp+fn)*(tn+fp)*(tn+fn))
    AUC = roc_auc_score(arrange_y_true, arrange_y_prob)
    f1 = 2*precision*recall/(precision+recall)
    print("loss_sum= ",loss_sum, "ACC= ",acc, "bacc= ",bacc, "precision= ",precision,"specificity= ",specificity, "sensitivity= ",sensitivity, "recall= ",recall, "MCC= ",MCC, "AUC= ",AUC, "f1= ",f1)
    return loss_sum, acc, bacc   # , precision, sensitivity, recall, MCC, AUC, f1


### esm2 2560 + MolFormer
different bottleneck size

#### bottle neck size 32

batch size 16

In [ ]:
import os
os.chdir('/content/drive/MyDrive/EC_number_kroll/esm2_2560')

In [ ]:
import torch
import torch.nn as nn

class Contrastive_learning_layer(nn.Module):
    def __init__(self):
        super().__init__()
        self.enzy_refine_layer_1 = nn.Linear(2560, 2560) # W1 and b
        self.smiles_refine_layer_1 = nn.Linear(768, 768) # W1 and b
        self.enzy_refine_layer_2 = nn.Linear(2560, 32) # W1 and b
        self.smiles_refine_layer_2 = nn.Linear(768, 32) # W1 and b

        self.relu = nn.ReLU()
        self.batch_norm_enzy = nn.BatchNorm1d(2560)
        self.batch_norm_smiles = nn.BatchNorm1d(768)
        self.batch_norm_shared = nn.BatchNorm1d(32)

    def forward(self, enzy_embed, smiles_embed):
        refined_enzy_embed = self.enzy_refine_layer_1(enzy_embed)
        refined_smiles_embed = self.smiles_refine_layer_1(smiles_embed)

        refined_enzy_embed = self.batch_norm_enzy(refined_enzy_embed)
        refined_smiles_embed = self.batch_norm_smiles(refined_smiles_embed)

        refined_enzy_embed = self.relu(refined_enzy_embed)
        refined_smiles_embed = self.relu(refined_smiles_embed)

        refined_enzy_embed = self.enzy_refine_layer_2(refined_enzy_embed)
        refined_smiles_embed = self.smiles_refine_layer_2(refined_smiles_embed)

        refined_enzy_embed = self.batch_norm_shared(refined_enzy_embed)
        refined_smiles_embed = self.batch_norm_shared(refined_smiles_embed)
        refined_enzy_embed = torch.nn.functional.normalize(refined_enzy_embed, dim=1)
        refined_smiles_embed = torch.nn.functional.normalize(refined_smiles_embed, dim=1)

        return refined_enzy_embed, refined_smiles_embed


In [ ]:
def get_ds():
    # Load the saved embeddings_results
    ESP_train_df_enzy = torch.load('ESP_train_df_enzy_esm2_2560.pt')
    ESP_val_df_enzy = torch.load('ESP_val_df_enzy_esm2_2560.pt')
    ESP_test_df_enzy = torch.load('ESP_test_df_enzy_esm2_2560.pt')
    print(ESP_train_df_enzy.shape, ESP_val_df_enzy.shape, ESP_test_df_enzy.shape)
    # Load the saved embeddings_results
    ESP_train_df_smiles = torch.load('ESP_train_df_smiles_esm2_2560.pt')
    ESP_val_df_smiles = torch.load('ESP_val_df_smiles_esm2_2560.pt')
    ESP_test_df_smiles = torch.load('ESP_test_df_smiles_esm2_2560.pt')
    print(ESP_train_df_smiles.shape, ESP_val_df_smiles.shape, ESP_test_df_smiles.shape)

    y_train = torch.load( 'ESP_train_df_label_esm2_2560.pt')
    y_val = torch.load('ESP_val_df_label_esm2_2560.pt')
    y_test = torch.load('ESP_test_df_label_esm2_2560.pt')
    print(y_train.shape,y_val.shape, y_test.shape)
    ESP_train_df_enzy_add = torch.load('ESP_train_df_enzy_>2800_<5500.pt')
    ESP_train_df_smiles_add = torch.load('ESP_train_df_smiles_>2800_<5500.pt')
    y_train_add = torch.load('ESP_train_df_label_>2800_<5500.pt')

    ESP_val_df_enzy_add = torch.load('ESP_val_df_enzy_>2800_<8000.pt')
    ESP_test_df_enzy_add = torch.load('ESP_test_df_enzy_>2800_<8000.pt')
    ESP_val_df_smiles_add = torch.load('ESP_val_df_smiles_>2800_<8000.pt')
    ESP_test_df_smiles_add = torch.load('ESP_test_df_smiles_>2800_<8000.pt')
    y_val_add = torch.load('ESP_val_df_label_>2800_<8000.pt')
    y_test_add = torch.load('ESP_test_df_label_>2800_<8000.pt')
    print(ESP_val_df_enzy_add.shape, ESP_val_df_smiles_add.shape, y_val_add.shape)
    print(ESP_test_df_enzy_add.shape, ESP_test_df_smiles_add.shape, y_test_add.shape)

    ESP_train_df_enzy = torch.cat([ESP_train_df_enzy, ESP_train_df_enzy_add], dim=0)
    ESP_train_df_smiles = torch.cat([ESP_train_df_smiles, ESP_train_df_smiles_add], dim=0)
    y_train = torch.cat([y_train, y_train_add], dim=0)
    print(ESP_train_df_enzy.shape, ESP_train_df_smiles.shape, y_train.shape)

    ESP_val_df_enzy = torch.cat([ESP_val_df_enzy, ESP_val_df_enzy_add], dim=0)
    ESP_val_df_smiles = torch.cat([ESP_val_df_smiles, ESP_val_df_smiles_add], dim=0)
    y_val = torch.cat([y_val, y_val_add], dim=0)
    print(ESP_val_df_enzy.shape, ESP_val_df_smiles.shape, y_val.shape)
    ESP_test_df_enzy = torch.cat([ESP_test_df_enzy, ESP_test_df_enzy_add], dim=0)
    ESP_test_df_smiles = torch.cat([ESP_test_df_smiles, ESP_test_df_smiles_add], dim=0)
    y_test = torch.cat([y_test, y_test_add], dim=0)
    print(ESP_test_df_enzy.shape, ESP_test_df_smiles.shape, y_test.shape)

    train_tensor_dataset = TensorDataset(ESP_train_df_enzy,ESP_train_df_smiles, y_train)
    val_tensor_dataset = TensorDataset(ESP_val_df_enzy,ESP_val_df_smiles, y_val)
    test_tensor_dataset = TensorDataset(ESP_test_df_enzy, ESP_test_df_smiles, y_test)

    # Create TensorDataset and DataLoaders
    batch_size = 16
    train_loader = DataLoader(train_tensor_dataset, batch_size=batch_size, shuffle=True)
    val_loader = DataLoader(val_tensor_dataset, batch_size=batch_size, shuffle=False)
    test_loader = DataLoader(test_tensor_dataset, batch_size=batch_size, shuffle=False)
    print(len(train_loader))
    return train_loader,  val_loader, test_loader

In [ ]:
# design the model, optimizer and loss function
model = Contrastive_learning_layer().to(device)
train_loader,  val_loader, test_loader = get_ds()
optimizer = torch.optim.Adam(model.parameters(),lr= 1e-03)
loss_fn = nn.MSELoss().to(device)

torch.Size([49881, 2560]) torch.Size([5399, 2560]) torch.Size([13312, 2560])
torch.Size([49881, 768]) torch.Size([5399, 768]) torch.Size([13312, 768])
torch.Size([49881, 1]) torch.Size([5399, 1]) torch.Size([13312, 1])
torch.Size([23, 2560]) torch.Size([23, 768]) torch.Size([23, 1])
torch.Size([24, 2560]) torch.Size([24, 768]) torch.Size([24, 1])
torch.Size([50061, 2560]) torch.Size([50061, 768]) torch.Size([50061, 1])
torch.Size([5422, 2560]) torch.Size([5422, 768]) torch.Size([5422, 1])
torch.Size([13336, 2560]) torch.Size([13336, 768]) torch.Size([13336, 1])
3129


In [ ]:
initial_epoch = 0
best_epoch = -1
best_accuracy = 0.5
for epoch in range(initial_epoch, 500):
    torch.cuda.empty_cache()
    model.train()
    with tqdm(train_loader, desc='Processing', unit="batch") as tepoch:
        for ESP_train_df_enzy,ESP_train_df_smiles, y_train in tepoch:
            model.train()
            tepoch.set_description(f"Epoch {epoch}")
            ESP_train_df_enzy = ESP_train_df_enzy.to(device)
            ESP_train_df_smiles = ESP_train_df_smiles.to(device)
            y_train = y_train.squeeze(1).to(device)
            refined_enzy_embed, refined_smiles_embed = model(ESP_train_df_enzy,ESP_train_df_smiles)
            cosine_sim = torch.nn.functional.cosine_similarity(refined_enzy_embed, refined_smiles_embed, dim=1)
            loss = loss_fn(cosine_sim, y_train)
            loss.backward()
            optimizer.step()
            optimizer.zero_grad(set_to_none=True) #
            tepoch.set_postfix(train_loss=loss)
            # tepoch.set_postfix(val_loss=loss_sum_val, val_accuracy=100. * acc_val, balanced_val_accuracy=100. * bacc_val)
        loss_sum_val,acc_val, bacc_val = run_validation(model,val_loader,loss_fn, device)
        print('Epoch: %d / %d, ############## the best accuracy in val  %.4f at Epoch: %d  ##############'  % (epoch, 500,100 * best_accuracy,best_epoch))
        # print('Performance in Train: Loss: (%.4f); Accuracy (%.2f)' % (loss_sum, 100 * acc))
        print('Performance in Val: Loss: (%.4f); Accuracy (%.2f)' % (loss_sum_val, 100 * acc_val))
        # checkpoint(model, f"epoch-{epoch}.pth")
        if acc_val > best_accuracy: # compare the performance updates at the val set
            best_accuracy = acc_val
            best_epoch = epoch
            torch.save(model, "best_model32.pt")

Epoch 0: 100%|██████████| 3129/3129 [00:30<00:00, 101.61batch/s, train_loss=tensor(0.0958, device='cuda:0', grad_fn=<MseLossBackward0>)]


loss_sum=  0.161300577379895 ACC=  0.7921431206196975 bacc=  0.6620263342345575 precision=  0.6895261845386533 specificity=  0.9376096216487096 sensitivity=  0.3864430468204053 recall=  0.3864430468204053 MCC=  0.4023167468747726 AUC=  0.7810686378383509 f1=  0.49529780564263315
Epoch: 0 / 500, ############## the best accuracy in val  50.0000 at Epoch: -1  ##############
Performance in Val: Loss: (0.1613); Accuracy (79.21)


Epoch 1: 100%|██████████| 3129/3129 [00:27<00:00, 112.91batch/s, train_loss=tensor(0.1075, device='cuda:0', grad_fn=<MseLossBackward0>)]


loss_sum=  0.1403690780153097 ACC=  0.8140907414238289 bacc=  0.6787278714634132 precision=  0.8025751072961373 specificity=  0.9654221999498872 sensitivity=  0.3920335429769392 recall=  0.3920335429769392 MCC=  0.47014887257054205 AUC=  0.836205799176729 f1=  0.5267605633802817
Epoch: 1 / 500, ############## the best accuracy in val  79.2143 at Epoch: 0  ##############
Performance in Val: Loss: (0.1404); Accuracy (81.41)


Epoch 2: 100%|██████████| 3129/3129 [00:28<00:00, 111.28batch/s, train_loss=tensor(0.1104, device='cuda:0', grad_fn=<MseLossBackward0>)]


...

loss_sum=  0.05780217628843621 ACC=  0.9382146809295463 bacc=  0.9132057436709886 precision=  0.9011713030746705 specificity=  0.9661738912553245 sensitivity=  0.8602375960866527 recall=  0.8602375960866527 MCC=  0.8390400726923071 AUC=  0.9598050015049584 f1=  0.8802288165892027
Epoch: 497 / 500, ############## the best accuracy in val  94.0612 at Epoch: 173  ##############
Performance in Val: Loss: (0.0578); Accuracy (93.82)


Epoch 498: 100%|██████████| 3129/3129 [00:28<00:00, 109.52batch/s, train_loss=tensor(0.0160, device='cuda:0', grad_fn=<MseLossBackward0>)]


loss_sum=  0.05701252660002548 ACC=  0.9374769457764662 bacc=  0.9115839955063113 precision=  0.9014705882352941 specificity=  0.9664244550238036 sensitivity=  0.856743535988819 recall=  0.856743535988819 MCC=  0.8369697108005237 AUC=  0.9609953982764505 f1=  0.878538158366177
Epoch: 498 / 500, ############## the best accuracy in val  94.0612 at Epoch: 173  ##############
Performance in Val: Loss: (0.0570); Accuracy (93.75)


Epoch 499: 100%|██████████| 3129/3129 [00:29<00:00, 106.99batch/s, train_loss=tensor(0.0122, device='cuda:0', grad_fn=<MseLossBackward0>)]


loss_sum=  0.05813587331391629 ACC=  0.9389524160826264 bacc=  0.9143792435845782 precision=  0.902046783625731 specificity=  0.9664244550238036 sensitivity=  0.8623340321453529 recall=  0.8623340321453529 MCC=  0.8410150137569676 AUC=  0.9602493976226384 f1=  0.8817434798142194
Epoch: 499 / 500, ############## the best accuracy in val  94.0612 at Epoch: 173  ##############
Performance in Val: Loss: (0.0581); Accuracy (93.90)


In [ ]:
import torch
# Specify the file path where the entire model is saved
load_path = 'best_model32.pt'
# Load the entire model
model_test = torch.load(load_path)
# model_test.to('cuda')
# rename the baseline model
torch.save(model_test, '5500_threshold_best_model_esm2_2560_botlle_neck32_batch_16_1.pt')
run_validation(model_test,test_loader,loss_fn, device) # performance evaluation

loss_sum=  0.06624889328999878 ACC=  0.9309388122375525 bacc=  0.9010702890944857 precision=  0.8935395814376706 specificity=  0.9642566191446028 sensitivity=  0.8378839590443686 recall=  0.8378839590443686 MCC=  0.8192679455786949 AUC=  0.9541067862016872 f1=  0.86481726111845


(0.06624889328999878, 0.9309388122375525, 0.9010702890944857)

#### bottle neck size 64

batch size 16

In [ ]:
import os
os.chdir('/content/drive/MyDrive/EC_number_kroll/esm2_2560')

In [ ]:
import torch
import torch.nn as nn

class Contrastive_learning_layer(nn.Module):
    def __init__(self):
        super().__init__()
        self.enzy_refine_layer_1 = nn.Linear(2560, 2560) # W1 and b
        self.smiles_refine_layer_1 = nn.Linear(768, 768) # W1 and b
        self.enzy_refine_layer_2 = nn.Linear(2560, 64) # W1 and b
        self.smiles_refine_layer_2 = nn.Linear(768, 64) # W1 and b

        self.relu = nn.ReLU()
        self.batch_norm_enzy = nn.BatchNorm1d(2560)
        self.batch_norm_smiles = nn.BatchNorm1d(768)
        self.batch_norm_shared = nn.BatchNorm1d(64)

    def forward(self, enzy_embed, smiles_embed):
        refined_enzy_embed = self.enzy_refine_layer_1(enzy_embed)
        refined_smiles_embed = self.smiles_refine_layer_1(smiles_embed)

        refined_enzy_embed = self.batch_norm_enzy(refined_enzy_embed)
        refined_smiles_embed = self.batch_norm_smiles(refined_smiles_embed)

        refined_enzy_embed = self.relu(refined_enzy_embed)
        refined_smiles_embed = self.relu(refined_smiles_embed)

        refined_enzy_embed = self.enzy_refine_layer_2(refined_enzy_embed)
        refined_smiles_embed = self.smiles_refine_layer_2(refined_smiles_embed)

        refined_enzy_embed = self.batch_norm_shared(refined_enzy_embed)
        refined_smiles_embed = self.batch_norm_shared(refined_smiles_embed)
        refined_enzy_embed = torch.nn.functional.normalize(refined_enzy_embed, dim=1)
        refined_smiles_embed = torch.nn.functional.normalize(refined_smiles_embed, dim=1)

        return refined_enzy_embed, refined_smiles_embed


In [ ]:
def get_ds():
    # Load the saved embeddings_results
    ESP_train_df_enzy = torch.load('ESP_train_df_enzy_esm2_2560.pt')
    ESP_val_df_enzy = torch.load('ESP_val_df_enzy_esm2_2560.pt')
    ESP_test_df_enzy = torch.load('ESP_test_df_enzy_esm2_2560.pt')
    print(ESP_train_df_enzy.shape, ESP_val_df_enzy.shape, ESP_test_df_enzy.shape)
    # Load the saved embeddings_results
    ESP_train_df_smiles = torch.load('ESP_train_df_smiles_esm2_2560.pt')
    ESP_val_df_smiles = torch.load('ESP_val_df_smiles_esm2_2560.pt')
    ESP_test_df_smiles = torch.load('ESP_test_df_smiles_esm2_2560.pt')
    print(ESP_train_df_smiles.shape, ESP_val_df_smiles.shape, ESP_test_df_smiles.shape)

    y_train = torch.load( 'ESP_train_df_label_esm2_2560.pt')
    y_val = torch.load('ESP_val_df_label_esm2_2560.pt')
    y_test = torch.load('ESP_test_df_label_esm2_2560.pt')
    print(y_train.shape,y_val.shape, y_test.shape)
    ESP_train_df_enzy_add = torch.load('ESP_train_df_enzy_>2800_<5500.pt')
    ESP_train_df_smiles_add = torch.load('ESP_train_df_smiles_>2800_<5500.pt')
    y_train_add = torch.load('ESP_train_df_label_>2800_<5500.pt')

    ESP_val_df_enzy_add = torch.load('ESP_val_df_enzy_>2800_<8000.pt')
    ESP_test_df_enzy_add = torch.load('ESP_test_df_enzy_>2800_<8000.pt')
    ESP_val_df_smiles_add = torch.load('ESP_val_df_smiles_>2800_<8000.pt')
    ESP_test_df_smiles_add = torch.load('ESP_test_df_smiles_>2800_<8000.pt')
    y_val_add = torch.load('ESP_val_df_label_>2800_<8000.pt')
    y_test_add = torch.load('ESP_test_df_label_>2800_<8000.pt')
    print(ESP_val_df_enzy_add.shape, ESP_val_df_smiles_add.shape, y_val_add.shape)
    print(ESP_test_df_enzy_add.shape, ESP_test_df_smiles_add.shape, y_test_add.shape)

    ESP_train_df_enzy = torch.cat([ESP_train_df_enzy, ESP_train_df_enzy_add], dim=0)
    ESP_train_df_smiles = torch.cat([ESP_train_df_smiles, ESP_train_df_smiles_add], dim=0)
    y_train = torch.cat([y_train, y_train_add], dim=0)
    print(ESP_train_df_enzy.shape, ESP_train_df_smiles.shape, y_train.shape)

    ESP_val_df_enzy = torch.cat([ESP_val_df_enzy, ESP_val_df_enzy_add], dim=0)
    ESP_val_df_smiles = torch.cat([ESP_val_df_smiles, ESP_val_df_smiles_add], dim=0)
    y_val = torch.cat([y_val, y_val_add], dim=0)
    print(ESP_val_df_enzy.shape, ESP_val_df_smiles.shape, y_val.shape)
    ESP_test_df_enzy = torch.cat([ESP_test_df_enzy, ESP_test_df_enzy_add], dim=0)
    ESP_test_df_smiles = torch.cat([ESP_test_df_smiles, ESP_test_df_smiles_add], dim=0)
    y_test = torch.cat([y_test, y_test_add], dim=0)
    print(ESP_test_df_enzy.shape, ESP_test_df_smiles.shape, y_test.shape)

    train_tensor_dataset = TensorDataset(ESP_train_df_enzy,ESP_train_df_smiles, y_train)
    val_tensor_dataset = TensorDataset(ESP_val_df_enzy,ESP_val_df_smiles, y_val)
    test_tensor_dataset = TensorDataset(ESP_test_df_enzy, ESP_test_df_smiles, y_test)

    # Create TensorDataset and DataLoaders
    batch_size = 16
    train_loader = DataLoader(train_tensor_dataset, batch_size=batch_size, shuffle=True)
    val_loader = DataLoader(val_tensor_dataset, batch_size=batch_size, shuffle=False)
    test_loader = DataLoader(test_tensor_dataset, batch_size=batch_size, shuffle=False)
    print(len(train_loader))
    return train_loader,  val_loader, test_loader

In [ ]:
# design the model, optimizer and loss function
model = Contrastive_learning_layer().to(device)
train_loader,  val_loader, test_loader = get_ds()
optimizer = torch.optim.Adam(model.parameters(),lr= 1e-03)
loss_fn = nn.MSELoss().to(device)

torch.Size([49881, 2560]) torch.Size([5399, 2560]) torch.Size([13312, 2560])
torch.Size([49881, 768]) torch.Size([5399, 768]) torch.Size([13312, 768])
torch.Size([49881, 1]) torch.Size([5399, 1]) torch.Size([13312, 1])
torch.Size([23, 2560]) torch.Size([23, 768]) torch.Size([23, 1])
torch.Size([24, 2560]) torch.Size([24, 768]) torch.Size([24, 1])
torch.Size([50061, 2560]) torch.Size([50061, 768]) torch.Size([50061, 1])
torch.Size([5422, 2560]) torch.Size([5422, 768]) torch.Size([5422, 1])
torch.Size([13336, 2560]) torch.Size([13336, 768]) torch.Size([13336, 1])
3129


In [ ]:
initial_epoch = 0
best_epoch = -1
best_accuracy = 0.5
for epoch in range(initial_epoch, 500):
    torch.cuda.empty_cache()
    model.train()
    with tqdm(train_loader, desc='Processing', unit="batch") as tepoch:
        for ESP_train_df_enzy,ESP_train_df_smiles, y_train in tepoch:
            model.train()
            tepoch.set_description(f"Epoch {epoch}")
            ESP_train_df_enzy = ESP_train_df_enzy.to(device)
            ESP_train_df_smiles = ESP_train_df_smiles.to(device)
            y_train = y_train.squeeze(1).to(device)
            refined_enzy_embed, refined_smiles_embed = model(ESP_train_df_enzy,ESP_train_df_smiles)
            cosine_sim = torch.nn.functional.cosine_similarity(refined_enzy_embed, refined_smiles_embed, dim=1)
            loss = loss_fn(cosine_sim, y_train)
            loss.backward()
            optimizer.step()
            optimizer.zero_grad(set_to_none=True) #
            tepoch.set_postfix(train_loss=loss)
            # tepoch.set_postfix(val_loss=loss_sum_val, val_accuracy=100. * acc_val, balanced_val_accuracy=100. * bacc_val)
        loss_sum_val,acc_val, bacc_val = run_validation(model,val_loader,loss_fn, device)
        print('Epoch: %d / %d, ############## the best accuracy in val  %.4f at Epoch: %d  ##############'  % (epoch, 500,100 * best_accuracy,best_epoch))
        # print('Performance in Train: Loss: (%.4f); Accuracy (%.2f)' % (loss_sum, 100 * acc))
        print('Performance in Val: Loss: (%.4f); Accuracy (%.2f)' % (loss_sum_val, 100 * acc_val))
        # checkpoint(model, f"epoch-{epoch}.pth")
        if acc_val > best_accuracy: # compare the performance updates at the val set
            best_accuracy = acc_val
            best_epoch = epoch
            torch.save(model, "best_model.pt")

Epoch 0: 100%|██████████| 3129/3129 [00:31<00:00, 98.48batch/s, train_loss=tensor(0.1904, device='cuda:0', grad_fn=<MseLossBackward0>)] 


loss_sum=  0.16584828437187854 ACC=  0.7705643673921062 bacc=  0.6144221073235885 precision=  0.6496 specificity=  0.9451265347030819 sensitivity=  0.283717679944095 recall=  0.283717679944095 MCC=  0.3158462685733902 AUC=  0.7812827814364289 f1=  0.3949416342412451
Epoch: 0 / 500, ############## the best accuracy in val  50.0000 at Epoch: -1  ##############
Performance in Val: Loss: (0.1658); Accuracy (77.06)


Epoch 1: 100%|██████████| 3129/3129 [00:31<00:00, 100.20batch/s, train_loss=tensor(0.1609, device='cuda:0', grad_fn=<MseLossBackward0>)]


loss_sum=  0.13044025827127792 ACC=  0.8233124308373294 bacc=  0.7026977715933527 precision=  0.7930607187112764 specificity=  0.958155850663994 sensitivity=  0.4472396925227114 recall=  0.4472396925227114 MCC=  0.5020153892193242 AUC=  0.8746059661492026 f1=  0.5719392314566578
Epoch: 1 / 500, ############## the best accuracy in val  77.0564 at Epoch: 0  ##############
Performance in Val: Loss: (0.1304); Accuracy (82.33)


Epoch 2: 100%|██████████| 3129/3129 [00:31<00:00, 99.93batch/s, train_loss=tensor(0.1196, device='cuda:0', grad_fn=<MseLossBackward0>)] 


loss_sum=  0.11452806276162114 ACC=  0.8524529693839912 bacc=  0.761489907147826 precision=  0.8164493480441324 specificity=  0.9541468303683287 sensitivity=  0.5688329839273235 recall=  0.5688329839273235 MCC=  0.5950334639683481 AUC=  0.8985867222914731 f1=  0.670510708401977
Epoch: 2 / 500, ############## the best accuracy in val  82.3312 at Epoch: 1  ##############
Performance in Val: Loss: (0.1145); Accuracy (85.25)


Epoch 3: 100%|██████████| 3129/3129 [00:31<00:00, 98.69batch/s, train_loss=tensor(0.0861, device='cuda:0', grad_fn=<MseLossBackward0>)]


loss_sum=  0.116355791611042 ACC=  0.8572482478790114 bacc=  0.7687814703978431 precision=  0.8262164846077458 specificity=  0.9561513405161614 sensitivity=  0.5814116002795248 recall=  0.5814116002795248 MCC=  0.6092701660335094 AUC=  0.8949413784088973 f1=  0.6825266611977031
Epoch: 3 / 500, ############## the best accuracy in val  85.2453 at Epoch: 2  ##############
Performance in Val: Loss: (0.1164); Accuracy (85.72)


Epoch 4:  89%|████████▉ | 2781/3129 [00:27<00:03, 100.05batch/s, train_loss=tensor(0.0525, device='cuda:0', grad_fn=<MseLossBackward0>)]

In [ ]:
import torch
# Specify the file path where the entire model is saved
load_path = 'best_model.pt'
# Load the entire model
model_test = torch.load(load_path)
# model_test.to('cuda')
# rename the baseline model
torch.save(model_test, '5500_threshold_best_model_esm2_2560_botlle_neck64_batch_16_1.pt')
run_validation(model_test,test_loader,loss_fn, device) # performance evaluation

loss_sum=  0.06466402248194669 ACC=  0.9301889622075585 bacc=  0.9019304824729082 precision=  0.8873239436619719 specificity=  0.9617107942973523 sensitivity=  0.8421501706484642 recall=  0.8421501706484642 MCC=  0.8177202065147982 AUC=  0.9563891949285084 f1=  0.8641470888661901


(0.06466402248194669, 0.9301889622075585, 0.9019304824729082)

#### bottle neck 128


In [ ]:
import os
os.chdir('/content/drive/MyDrive/EC_number_kroll/esm2_2560')

In [ ]:
import torch
import torch.nn as nn

class Contrastive_learning_layer(nn.Module):
    def __init__(self):
        super().__init__()
        self.enzy_refine_layer_1 = nn.Linear(2560, 2560) # W1 and b
        self.smiles_refine_layer_1 = nn.Linear(768, 768) # W1 and b
        self.enzy_refine_layer_2 = nn.Linear(2560, 128) # W1 and b
        self.smiles_refine_layer_2 = nn.Linear(768, 128) # W1 and b

        self.relu = nn.ReLU()
        self.batch_norm_enzy = nn.BatchNorm1d(2560)
        self.batch_norm_smiles = nn.BatchNorm1d(768)
        self.batch_norm_shared = nn.BatchNorm1d(128)

    def forward(self, enzy_embed, smiles_embed):
        refined_enzy_embed = self.enzy_refine_layer_1(enzy_embed)
        refined_smiles_embed = self.smiles_refine_layer_1(smiles_embed)

        refined_enzy_embed = self.batch_norm_enzy(refined_enzy_embed)
        refined_smiles_embed = self.batch_norm_smiles(refined_smiles_embed)

        refined_enzy_embed = self.relu(refined_enzy_embed)
        refined_smiles_embed = self.relu(refined_smiles_embed)

        refined_enzy_embed = self.enzy_refine_layer_2(refined_enzy_embed)
        refined_smiles_embed = self.smiles_refine_layer_2(refined_smiles_embed)

        refined_enzy_embed = self.batch_norm_shared(refined_enzy_embed)
        refined_smiles_embed = self.batch_norm_shared(refined_smiles_embed)
        refined_enzy_embed = torch.nn.functional.normalize(refined_enzy_embed, dim=1)
        refined_smiles_embed = torch.nn.functional.normalize(refined_smiles_embed, dim=1)

        return refined_enzy_embed, refined_smiles_embed


In [ ]:
def get_ds():
    # Load the saved embeddings_results
    ESP_train_df_enzy = torch.load('ESP_train_df_enzy_esm2_2560.pt')
    ESP_val_df_enzy = torch.load('ESP_val_df_enzy_esm2_2560.pt')
    ESP_test_df_enzy = torch.load('ESP_test_df_enzy_esm2_2560.pt')
    print(ESP_train_df_enzy.shape, ESP_val_df_enzy.shape, ESP_test_df_enzy.shape)
    # Load the saved embeddings_results
    ESP_train_df_smiles = torch.load('ESP_train_df_smiles_esm2_2560.pt')
    ESP_val_df_smiles = torch.load('ESP_val_df_smiles_esm2_2560.pt')
    ESP_test_df_smiles = torch.load('ESP_test_df_smiles_esm2_2560.pt')
    print(ESP_train_df_smiles.shape, ESP_val_df_smiles.shape, ESP_test_df_smiles.shape)

    y_train = torch.load( 'ESP_train_df_label_esm2_2560.pt')
    y_val = torch.load('ESP_val_df_label_esm2_2560.pt')
    y_test = torch.load('ESP_test_df_label_esm2_2560.pt')
    print(y_train.shape,y_val.shape, y_test.shape)
    ESP_train_df_enzy_add = torch.load('ESP_train_df_enzy_>2800_<5500.pt')
    ESP_train_df_smiles_add = torch.load('ESP_train_df_smiles_>2800_<5500.pt')
    y_train_add = torch.load('ESP_train_df_label_>2800_<5500.pt')

    ESP_val_df_enzy_add = torch.load('ESP_val_df_enzy_>2800_<8000.pt')
    ESP_test_df_enzy_add = torch.load('ESP_test_df_enzy_>2800_<8000.pt')
    ESP_val_df_smiles_add = torch.load('ESP_val_df_smiles_>2800_<8000.pt')
    ESP_test_df_smiles_add = torch.load('ESP_test_df_smiles_>2800_<8000.pt')
    y_val_add = torch.load('ESP_val_df_label_>2800_<8000.pt')
    y_test_add = torch.load('ESP_test_df_label_>2800_<8000.pt')
    print(ESP_val_df_enzy_add.shape, ESP_val_df_smiles_add.shape, y_val_add.shape)
    print(ESP_test_df_enzy_add.shape, ESP_test_df_smiles_add.shape, y_test_add.shape)

    ESP_train_df_enzy = torch.cat([ESP_train_df_enzy, ESP_train_df_enzy_add], dim=0)
    ESP_train_df_smiles = torch.cat([ESP_train_df_smiles, ESP_train_df_smiles_add], dim=0)
    y_train = torch.cat([y_train, y_train_add], dim=0)
    print(ESP_train_df_enzy.shape, ESP_train_df_smiles.shape, y_train.shape)

    ESP_val_df_enzy = torch.cat([ESP_val_df_enzy, ESP_val_df_enzy_add], dim=0)
    ESP_val_df_smiles = torch.cat([ESP_val_df_smiles, ESP_val_df_smiles_add], dim=0)
    y_val = torch.cat([y_val, y_val_add], dim=0)
    print(ESP_val_df_enzy.shape, ESP_val_df_smiles.shape, y_val.shape)
    ESP_test_df_enzy = torch.cat([ESP_test_df_enzy, ESP_test_df_enzy_add], dim=0)
    ESP_test_df_smiles = torch.cat([ESP_test_df_smiles, ESP_test_df_smiles_add], dim=0)
    y_test = torch.cat([y_test, y_test_add], dim=0)
    print(ESP_test_df_enzy.shape, ESP_test_df_smiles.shape, y_test.shape)

    train_tensor_dataset = TensorDataset(ESP_train_df_enzy,ESP_train_df_smiles, y_train)
    val_tensor_dataset = TensorDataset(ESP_val_df_enzy,ESP_val_df_smiles, y_val)
    test_tensor_dataset = TensorDataset(ESP_test_df_enzy, ESP_test_df_smiles, y_test)

    # Create TensorDataset and DataLoaders
    batch_size = 16
    train_loader = DataLoader(train_tensor_dataset, batch_size=batch_size, shuffle=True)
    val_loader = DataLoader(val_tensor_dataset, batch_size=batch_size, shuffle=False)
    test_loader = DataLoader(test_tensor_dataset, batch_size=batch_size, shuffle=False)
    print(len(train_loader))
    return train_loader,  val_loader, test_loader

In [ ]:
# design the model, optimizer and loss function
model = Contrastive_learning_layer().to(device)
train_loader,  val_loader, test_loader = get_ds()
optimizer = torch.optim.Adam(model.parameters(),lr= 1e-03)
loss_fn = nn.MSELoss().to(device)

torch.Size([49881, 2560]) torch.Size([5399, 2560]) torch.Size([13312, 2560])
torch.Size([49881, 768]) torch.Size([5399, 768]) torch.Size([13312, 768])
torch.Size([49881, 1]) torch.Size([5399, 1]) torch.Size([13312, 1])
torch.Size([23, 2560]) torch.Size([23, 768]) torch.Size([23, 1])
torch.Size([24, 2560]) torch.Size([24, 768]) torch.Size([24, 1])
torch.Size([50061, 2560]) torch.Size([50061, 768]) torch.Size([50061, 1])
torch.Size([5422, 2560]) torch.Size([5422, 768]) torch.Size([5422, 1])
torch.Size([13336, 2560]) torch.Size([13336, 768]) torch.Size([13336, 1])
3129


In [ ]:
initial_epoch = 0
best_epoch = -1
best_accuracy = 0.5
loss_train = []
loss_valid = []
for epoch in range(initial_epoch, 500):
    torch.cuda.empty_cache()
    model.train()

    with tqdm(train_loader, desc='Processing', unit="batch") as tepoch:
        num_batch = len(train_loader)
        loss_sum = 0
        for ESP_train_df_enzy,ESP_train_df_smiles, y_train in tepoch:
            model.train()
            tepoch.set_description(f"Epoch {epoch}")
            ESP_train_df_enzy = ESP_train_df_enzy.to(device)
            ESP_train_df_smiles = ESP_train_df_smiles.to(device)
            y_train = y_train.squeeze(1).to(device)
            refined_enzy_embed, refined_smiles_embed = model(ESP_train_df_enzy,ESP_train_df_smiles)
            cosine_sim = torch.nn.functional.cosine_similarity(refined_enzy_embed, refined_smiles_embed, dim=1)
            loss = loss_fn(cosine_sim, y_train)
            loss_sum = loss_sum + loss.detach().cpu().numpy()
            loss.backward()
            optimizer.step()
            optimizer.zero_grad(set_to_none=True) #
            tepoch.set_postfix(train_loss=loss)
            # tepoch.set_postfix(val_loss=loss_sum_val, val_accuracy=100. * acc_val, balanced_val_accuracy=100. * bacc_val)
        loss_sum = loss_sum/num_batch
        loss_train.append(loss_sum)
        loss_sum_val,acc_val, bacc_val = run_validation(model,val_loader,loss_fn, device)
        loss_valid.append(loss_sum_val)
        print('Epoch: %d / %d, ############## the best accuracy in val  %.4f at Epoch: %d  ##############'  % (epoch, 500,100 * best_accuracy,best_epoch))
        # print('Performance in Train: Loss: (%.4f); Accuracy (%.2f)' % (loss_sum, 100 * acc))
        print('Performance in Val: Loss: (%.4f); Accuracy (%.2f)' % (loss_sum_val, 100 * acc_val))
        # checkpoint(model, f"epoch-{epoch}.pth")
        if acc_val > best_accuracy: # compare the performance updates at the val set
            best_accuracy = acc_val
            best_epoch = epoch
            torch.save(model, "best_model_11.pt")

Epoch 0: 100%|██████████| 3129/3129 [00:29<00:00, 105.70batch/s, train_loss=tensor(0.2574, device='cuda:0', grad_fn=<MseLossBackward0>)]


loss_sum=  0.15453473258774542 ACC=  0.7897454813721874 bacc=  0.6328304022975525 precision=  0.7557117750439367 specificity=  0.9651716361814082 sensitivity=  0.3004891684136967 recall=  0.3004891684136967 MCC=  0.38205587781106 AUC=  0.8128040887244378 f1=  0.43
Epoch: 0 / 500, ############## the best accuracy in val  50.0000 at Epoch: -1  ##############
Performance in Val: Loss: (0.1545); Accuracy (78.97)


Epoch 1: 100%|██████████| 3129/3129 [00:29<00:00, 104.75batch/s, train_loss=tensor(0.1404, device='cuda:0', grad_fn=<MseLossBackward0>)]


loss_sum=  0.12694340112968006 ACC=  0.8284765769088898 bacc=  0.7055332919754282 precision=  0.8240620957309185 specificity=  0.9659233274868454 sensitivity=  0.4451432564640112 recall=  0.4451432564640112 MCC=  0.5182070709686368 AUC=  0.8796447317435578 f1=  0.5780399274047188
Epoch: 1 / 500, ############## the best accuracy in val  78.9745 at Epoch: 0  ##############
Performance in Val: Loss: (0.1269); Accuracy (82.85)


Epoch 2: 100%|██████████| 3129/3129 [00:29<00:00, 104.81batch/s, train_loss=tensor(0.1004, device='cuda:0', grad_fn=<MseLossBackward0>)]


...

loss_sum=  0.055989245178073556 ACC=  0.9402434526005164 bacc=  0.9127908513932729 precision=  0.9133681852128454 specificity=  0.970934602856427 sensitivity=  0.8546470999301188 recall=  0.8546470999301188 MCC=  0.8438024101208552 AUC=  0.9629408131958682 f1=  0.8830324909747292
Epoch: 497 / 500, ############## the best accuracy in val  94.2641 at Epoch: 483  ##############
Performance in Val: Loss: (0.0560); Accuracy (94.02)


Epoch 498: 100%|██████████| 3129/3129 [00:30<00:00, 102.94batch/s, train_loss=tensor(0.0146, device='cuda:0', grad_fn=<MseLossBackward0>)]


loss_sum=  0.055180798875371265 ACC=  0.9422722242714865 bacc=  0.915065448622083 precision=  0.9184131736526946 specificity=  0.9726885492357805 sensitivity=  0.8574423480083857 recall=  0.8574423480083857 MCC=  0.8490921954817683 AUC=  0.9646719969687212 f1=  0.8868810986628117
Epoch: 498 / 500, ############## the best accuracy in val  94.2641 at Epoch: 483  ##############
Performance in Val: Loss: (0.0552); Accuracy (94.23)


Epoch 499: 100%|██████████| 3129/3129 [00:30<00:00, 101.22batch/s, train_loss=tensor(0.0125, device='cuda:0', grad_fn=<MseLossBackward0>)]


loss_sum=  0.05603941356774233 ACC=  0.9406123201770564 bacc=  0.9150585322916465 precision=  0.9092250922509225 specificity=  0.9691806564770734 sensitivity=  0.8609364081062194 recall=  0.8609364081062194 MCC=  0.8450711755279224 AUC=  0.9636193139665576 f1=  0.8844221105527639
Epoch: 499 / 500, ############## the best accuracy in val  94.2641 at Epoch: 483  ##############
Performance in Val: Loss: (0.0560); Accuracy (94.06)


In [ ]:
import torch
# Specify the file path where the entire model is saved
load_path = 'best_model_11.pt'
# Load the entire model
model_test = torch.load(load_path)
# model_test.to('cuda')
# rename the baseline model
torch.save(model_test, 'best_model_esm2_2560_add_>2800_<8000_in_valid2.pt')
run_validation(model_test,test_loader,loss_fn, device) # performance evaluation

loss_sum=  0.06158351360281988 ACC=  0.9356628674265147 bacc=  0.9051909339672698 precision=  0.9084204056545789 specificity=  0.969653767820774 sensitivity=  0.8407281001137656 recall=  0.8407281001137656 MCC=  0.8313574088968375 AUC=  0.9593826968481587 f1=  0.8732644017725258


(0.06158351360281988, 0.9356628674265147, 0.9051909339672698)

#### large bottle neck size 256


In [ ]:
import os
os.chdir('/content/drive/MyDrive/EC_number_kroll/esm2_2560')

In [ ]:
import torch
import torch.nn as nn

class Contrastive_learning_layer(nn.Module):
    def __init__(self):
        super().__init__()
        self.enzy_refine_layer_1 = nn.Linear(2560, 2560) # W1 and b
        self.smiles_refine_layer_1 = nn.Linear(768, 768) # W1 and b
        self.enzy_refine_layer_2 = nn.Linear(2560, 256) # W1 and b
        self.smiles_refine_layer_2 = nn.Linear(768, 256) # W1 and b

        self.relu = nn.ReLU()
        self.batch_norm_enzy = nn.BatchNorm1d(2560)
        self.batch_norm_smiles = nn.BatchNorm1d(768)
        self.batch_norm_shared = nn.BatchNorm1d(256)

    def forward(self, enzy_embed, smiles_embed):
        refined_enzy_embed = self.enzy_refine_layer_1(enzy_embed)
        refined_smiles_embed = self.smiles_refine_layer_1(smiles_embed)

        refined_enzy_embed = self.batch_norm_enzy(refined_enzy_embed)
        refined_smiles_embed = self.batch_norm_smiles(refined_smiles_embed)

        refined_enzy_embed = self.relu(refined_enzy_embed)
        refined_smiles_embed = self.relu(refined_smiles_embed)

        refined_enzy_embed = self.enzy_refine_layer_2(refined_enzy_embed)
        refined_smiles_embed = self.smiles_refine_layer_2(refined_smiles_embed)

        refined_enzy_embed = self.batch_norm_shared(refined_enzy_embed)
        refined_smiles_embed = self.batch_norm_shared(refined_smiles_embed)
        refined_enzy_embed = torch.nn.functional.normalize(refined_enzy_embed, dim=1)
        refined_smiles_embed = torch.nn.functional.normalize(refined_smiles_embed, dim=1)

        return refined_enzy_embed, refined_smiles_embed


In [ ]:
def get_ds():
    # Load the saved embeddings_results
    ESP_train_df_enzy = torch.load('ESP_train_df_enzy_esm2_2560.pt')
    ESP_val_df_enzy = torch.load('ESP_val_df_enzy_esm2_2560.pt')
    ESP_test_df_enzy = torch.load('ESP_test_df_enzy_esm2_2560.pt')
    print(ESP_train_df_enzy.shape, ESP_val_df_enzy.shape, ESP_test_df_enzy.shape)
    # Load the saved embeddings_results
    ESP_train_df_smiles = torch.load('ESP_train_df_smiles_esm2_2560.pt')
    ESP_val_df_smiles = torch.load('ESP_val_df_smiles_esm2_2560.pt')
    ESP_test_df_smiles = torch.load('ESP_test_df_smiles_esm2_2560.pt')
    print(ESP_train_df_smiles.shape, ESP_val_df_smiles.shape, ESP_test_df_smiles.shape)

    y_train = torch.load( 'ESP_train_df_label_esm2_2560.pt')
    y_val = torch.load('ESP_val_df_label_esm2_2560.pt')
    y_test = torch.load('ESP_test_df_label_esm2_2560.pt')
    print(y_train.shape,y_val.shape, y_test.shape)
    ESP_train_df_enzy_add = torch.load('ESP_train_df_enzy_>2800_<5500.pt')
    ESP_train_df_smiles_add = torch.load('ESP_train_df_smiles_>2800_<5500.pt')
    y_train_add = torch.load('ESP_train_df_label_>2800_<5500.pt')

    ESP_val_df_enzy_add = torch.load('ESP_val_df_enzy_>2800_<8000.pt')
    ESP_test_df_enzy_add = torch.load('ESP_test_df_enzy_>2800_<8000.pt')
    ESP_val_df_smiles_add = torch.load('ESP_val_df_smiles_>2800_<8000.pt')
    ESP_test_df_smiles_add = torch.load('ESP_test_df_smiles_>2800_<8000.pt')
    y_val_add = torch.load('ESP_val_df_label_>2800_<8000.pt')
    y_test_add = torch.load('ESP_test_df_label_>2800_<8000.pt')
    print(ESP_val_df_enzy_add.shape, ESP_val_df_smiles_add.shape, y_val_add.shape)
    print(ESP_test_df_enzy_add.shape, ESP_test_df_smiles_add.shape, y_test_add.shape)

    ESP_train_df_enzy = torch.cat([ESP_train_df_enzy, ESP_train_df_enzy_add], dim=0)
    ESP_train_df_smiles = torch.cat([ESP_train_df_smiles, ESP_train_df_smiles_add], dim=0)
    y_train = torch.cat([y_train, y_train_add], dim=0)
    print(ESP_train_df_enzy.shape, ESP_train_df_smiles.shape, y_train.shape)

    ESP_val_df_enzy = torch.cat([ESP_val_df_enzy, ESP_val_df_enzy_add], dim=0)
    ESP_val_df_smiles = torch.cat([ESP_val_df_smiles, ESP_val_df_smiles_add], dim=0)
    y_val = torch.cat([y_val, y_val_add], dim=0)
    print(ESP_val_df_enzy.shape, ESP_val_df_smiles.shape, y_val.shape)
    ESP_test_df_enzy = torch.cat([ESP_test_df_enzy, ESP_test_df_enzy_add], dim=0)
    ESP_test_df_smiles = torch.cat([ESP_test_df_smiles, ESP_test_df_smiles_add], dim=0)
    y_test = torch.cat([y_test, y_test_add], dim=0)
    print(ESP_test_df_enzy.shape, ESP_test_df_smiles.shape, y_test.shape)

    train_tensor_dataset = TensorDataset(ESP_train_df_enzy,ESP_train_df_smiles, y_train)
    val_tensor_dataset = TensorDataset(ESP_val_df_enzy,ESP_val_df_smiles, y_val)
    test_tensor_dataset = TensorDataset(ESP_test_df_enzy, ESP_test_df_smiles, y_test)

    # Create TensorDataset and DataLoaders
    batch_size = 16
    train_loader = DataLoader(train_tensor_dataset, batch_size=batch_size, shuffle=True)
    val_loader = DataLoader(val_tensor_dataset, batch_size=batch_size, shuffle=False)
    test_loader = DataLoader(test_tensor_dataset, batch_size=batch_size, shuffle=False)
    print(len(train_loader))
    return train_loader,  val_loader, test_loader

In [ ]:
# design the model, optimizer and loss function
model = Contrastive_learning_layer().to(device)
train_loader,  val_loader, test_loader = get_ds()
optimizer = torch.optim.Adam(model.parameters(),lr= 1e-03)
loss_fn = nn.MSELoss().to(device)

torch.Size([49881, 2560]) torch.Size([5399, 2560]) torch.Size([13312, 2560])
torch.Size([49881, 768]) torch.Size([5399, 768]) torch.Size([13312, 768])
torch.Size([49881, 1]) torch.Size([5399, 1]) torch.Size([13312, 1])
torch.Size([23, 2560]) torch.Size([23, 768]) torch.Size([23, 1])
torch.Size([24, 2560]) torch.Size([24, 768]) torch.Size([24, 1])
torch.Size([50061, 2560]) torch.Size([50061, 768]) torch.Size([50061, 1])
torch.Size([5422, 2560]) torch.Size([5422, 768]) torch.Size([5422, 1])
torch.Size([13336, 2560]) torch.Size([13336, 768]) torch.Size([13336, 1])
3129


In [ ]:
initial_epoch = 0
best_epoch = -1
best_accuracy = 0.5
for epoch in range(initial_epoch, 500):
    torch.cuda.empty_cache()
    model.train()
    with tqdm(train_loader, desc='Processing', unit="batch") as tepoch:
        for ESP_train_df_enzy,ESP_train_df_smiles, y_train in tepoch:
            model.train()
            tepoch.set_description(f"Epoch {epoch}")
            ESP_train_df_enzy = ESP_train_df_enzy.to(device)
            ESP_train_df_smiles = ESP_train_df_smiles.to(device)
            y_train = y_train.squeeze(1).to(device)
            refined_enzy_embed, refined_smiles_embed = model(ESP_train_df_enzy,ESP_train_df_smiles)
            cosine_sim = torch.nn.functional.cosine_similarity(refined_enzy_embed, refined_smiles_embed, dim=1)
            loss = loss_fn(cosine_sim, y_train)
            loss.backward()
            optimizer.step()
            optimizer.zero_grad(set_to_none=True) #
            tepoch.set_postfix(train_loss=loss)
            # tepoch.set_postfix(val_loss=loss_sum_val, val_accuracy=100. * acc_val, balanced_val_accuracy=100. * bacc_val)
        loss_sum_val,acc_val, bacc_val = run_validation(model,val_loader,loss_fn, device)
        print('Epoch: %d / %d, ############## the best accuracy in val  %.4f at Epoch: %d  ##############'  % (epoch, 500,100 * best_accuracy,best_epoch))
        # print('Performance in Train: Loss: (%.4f); Accuracy (%.2f)' % (loss_sum, 100 * acc))
        print('Performance in Val: Loss: (%.4f); Accuracy (%.2f)' % (loss_sum_val, 100 * acc_val))
        # checkpoint(model, f"epoch-{epoch}.pth")
        if acc_val > best_accuracy: # compare the performance updates at the val set
            best_accuracy = acc_val
            best_epoch = epoch
            torch.save(model, "best_model.pt")

Epoch 0: 100%|██████████| 3129/3129 [00:30<00:00, 103.04batch/s, train_loss=tensor(0.2120, device='cuda:0', grad_fn=<MseLossBackward0>)]


loss_sum=  0.1555376641760006 ACC=  0.7908520841018074 bacc=  0.6546497614041096 precision=  0.6977363515312917 specificity=  0.9431220245552493 sensitivity=  0.36617749825296997 recall=  0.36617749825296997 MCC=  0.3946526547771724 AUC=  0.799131991775345 f1=  0.48029330889092586
Epoch: 0 / 500, ############## the best accuracy in val  50.0000 at Epoch: -1  ##############
Performance in Val: Loss: (0.1555); Accuracy (79.09)


Epoch 1: 100%|██████████| 3129/3129 [00:29<00:00, 104.45batch/s, train_loss=tensor(0.1478, device='cuda:0', grad_fn=<MseLossBackward0>)]


loss_sum=  0.14117934232561197 ACC=  0.8120619697528587 bacc=  0.6710742952215512 precision=  0.8149847094801224 specificity=  0.9696817840140316 sensitivity=  0.3724668064290706 recall=  0.3724668064290706 MCC=  0.46303992426693996 AUC=  0.8452500831272879 f1=  0.5112709832134292
Epoch: 1 / 500, ############## the best accuracy in val  79.0852 at Epoch: 0  ##############
Performance in Val: Loss: (0.1412); Accuracy (81.21)


Epoch 2: 100%|██████████| 3129/3129 [00:29<00:00, 104.66batch/s, train_loss=tensor(0.0884, device='cuda:0', grad_fn=<MseLossBackward0>)]


...

loss_sum=  0.056438532166161015 ACC=  0.9387679822943563 bacc=  0.9117885963193566 precision=  0.9079435783221975 specificity=  0.9689300927085943 sensitivity=  0.8546470999301188 recall=  0.8546470999301188 MCC=  0.8400736980400425 AUC=  0.9618830523814852 f1=  0.8804895608351332
Epoch: 497 / 500, ############## the best accuracy in val  94.2457 at Epoch: 250  ##############
Performance in Val: Loss: (0.0564); Accuracy (93.88)


Epoch 498: 100%|██████████| 3129/3129 [00:31<00:00, 100.79batch/s, train_loss=tensor(0.0217, device='cuda:0', grad_fn=<MseLossBackward0>)]


loss_sum=  0.05686929712077509 ACC=  0.9400590188122464 bacc=  0.9140103142622963 precision=  0.9090236686390533 specificity=  0.9691806564770734 sensitivity=  0.8588399720475192 recall=  0.8588399720475192 MCC=  0.8435605996796083 AUC=  0.9601714794696173 f1=  0.8832195472511677
Epoch: 498 / 500, ############## the best accuracy in val  94.2457 at Epoch: 250  ##############
Performance in Val: Loss: (0.0569); Accuracy (94.01)


Epoch 499: 100%|██████████| 3129/3129 [00:30<00:00, 102.26batch/s, train_loss=tensor(0.0119, device='cuda:0', grad_fn=<MseLossBackward0>)]


loss_sum=  0.05627962168729191 ACC=  0.9396901512357064 bacc=  0.914207998744905 precision=  0.906480117820324 specificity=  0.9681784014031571 sensitivity=  0.8602375960866527 recall=  0.8602375960866527 MCC=  0.8427182964640848 AUC=  0.9610368087105843 f1=  0.8827536751523845
Epoch: 499 / 500, ############## the best accuracy in val  94.2457 at Epoch: 250  ##############
Performance in Val: Loss: (0.0563); Accuracy (93.97)


In [ ]:
import torch
# Specify the file path where the entire model is saved
load_path = 'best_model.pt'
# Load the entire model
model_test = torch.load(load_path)
# model_test.to('cuda')
# rename the baseline model
torch.save(model_test, '5500_threshold_best_model_esm2_2560_botlle_neck256_batch_size_16.pt')
run_validation(model_test,test_loader,loss_fn, device) # performance evaluation

loss_sum=  0.06331703872632066 ACC=  0.9337882423515297 bacc=  0.9051047987784675 precision=  0.8983358547655068 specificity=  0.9657841140529532 sensitivity=  0.8444254835039818 recall=  0.8444254835039818 MCC=  0.8268366398699216 AUC=  0.9574376461170233 f1=  0.8705468406392025


(0.06331703872632066, 0.9337882423515297, 0.9051047987784675)

#### large bottle neck size 512


In [16]:
import os
os.chdir('/content/drive/MyDrive/EC_number_kroll/esm2_2560')

In [17]:
import torch
import torch.nn as nn

class Contrastive_learning_layer(nn.Module):
    def __init__(self):
        super().__init__()
        self.enzy_refine_layer_1 = nn.Linear(2560, 2560) # W1 and b
        self.smiles_refine_layer_1 = nn.Linear(768, 768) # W1 and b
        self.enzy_refine_layer_2 = nn.Linear(2560, 512) # W1 and b
        self.smiles_refine_layer_2 = nn.Linear(768, 512) # W1 and b

        self.relu = nn.ReLU()
        self.batch_norm_enzy = nn.BatchNorm1d(2560)
        self.batch_norm_smiles = nn.BatchNorm1d(768)
        self.batch_norm_shared = nn.BatchNorm1d(512)

    def forward(self, enzy_embed, smiles_embed):
        refined_enzy_embed = self.enzy_refine_layer_1(enzy_embed)
        refined_smiles_embed = self.smiles_refine_layer_1(smiles_embed)

        refined_enzy_embed = self.batch_norm_enzy(refined_enzy_embed)
        refined_smiles_embed = self.batch_norm_smiles(refined_smiles_embed)

        refined_enzy_embed = self.relu(refined_enzy_embed)
        refined_smiles_embed = self.relu(refined_smiles_embed)

        refined_enzy_embed = self.enzy_refine_layer_2(refined_enzy_embed)
        refined_smiles_embed = self.smiles_refine_layer_2(refined_smiles_embed)

        refined_enzy_embed = self.batch_norm_shared(refined_enzy_embed)
        refined_smiles_embed = self.batch_norm_shared(refined_smiles_embed)
        refined_enzy_embed = torch.nn.functional.normalize(refined_enzy_embed, dim=1)
        refined_smiles_embed = torch.nn.functional.normalize(refined_smiles_embed, dim=1)

        return refined_enzy_embed, refined_smiles_embed


In [18]:
def get_ds():
    # Load the saved embeddings_results
    ESP_train_df_enzy = torch.load('ESP_train_df_enzy_esm2_2560.pt')
    ESP_val_df_enzy = torch.load('ESP_val_df_enzy_esm2_2560.pt')
    ESP_test_df_enzy = torch.load('ESP_test_df_enzy_esm2_2560.pt')
    print(ESP_train_df_enzy.shape, ESP_val_df_enzy.shape, ESP_test_df_enzy.shape)
    # Load the saved embeddings_results
    ESP_train_df_smiles = torch.load('ESP_train_df_smiles_esm2_2560.pt')
    ESP_val_df_smiles = torch.load('ESP_val_df_smiles_esm2_2560.pt')
    ESP_test_df_smiles = torch.load('ESP_test_df_smiles_esm2_2560.pt')
    print(ESP_train_df_smiles.shape, ESP_val_df_smiles.shape, ESP_test_df_smiles.shape)

    y_train = torch.load( 'ESP_train_df_label_esm2_2560.pt')
    y_val = torch.load('ESP_val_df_label_esm2_2560.pt')
    y_test = torch.load('ESP_test_df_label_esm2_2560.pt')
    print(y_train.shape,y_val.shape, y_test.shape)


    train_tensor_dataset = TensorDataset(ESP_train_df_enzy,ESP_train_df_smiles, y_train)
    val_tensor_dataset = TensorDataset(ESP_val_df_enzy,ESP_val_df_smiles, y_val)
    test_tensor_dataset = TensorDataset(ESP_test_df_enzy, ESP_test_df_smiles, y_test)

    # Create TensorDataset and DataLoaders
    batch_size = 32
    train_loader = DataLoader(train_tensor_dataset, batch_size=batch_size, shuffle=True)
    val_loader = DataLoader(val_tensor_dataset, batch_size=batch_size, shuffle=False)
    test_loader = DataLoader(test_tensor_dataset, batch_size=batch_size, shuffle=False)
    print(len(train_loader))
    return train_loader,  val_loader, test_loader

In [19]:
# design the model, optimizer and loss function
model = Contrastive_learning_layer().to(device)
train_loader,  val_loader, test_loader = get_ds()
optimizer = torch.optim.Adam(model.parameters(),lr= 1e-03)
loss_fn = nn.MSELoss().to(device)

torch.Size([49881, 2560]) torch.Size([5399, 2560]) torch.Size([13312, 2560])
torch.Size([49881, 768]) torch.Size([5399, 768]) torch.Size([13312, 768])
torch.Size([49881, 1]) torch.Size([5399, 1]) torch.Size([13312, 1])
1559


In [20]:
initial_epoch = 0
best_epoch = -1
best_accuracy = 0.5
for epoch in range(initial_epoch, 500):
    torch.cuda.empty_cache()
    model.train()
    with tqdm(train_loader, desc='Processing', unit="batch") as tepoch:
        for ESP_train_df_enzy,ESP_train_df_smiles, y_train in tepoch:
            model.train()
            tepoch.set_description(f"Epoch {epoch}")
            ESP_train_df_enzy = ESP_train_df_enzy.to(device)
            ESP_train_df_smiles = ESP_train_df_smiles.to(device)
            y_train = y_train.squeeze(1).to(device)
            refined_enzy_embed, refined_smiles_embed = model(ESP_train_df_enzy,ESP_train_df_smiles)
            cosine_sim = torch.nn.functional.cosine_similarity(refined_enzy_embed, refined_smiles_embed, dim=1)
            loss = loss_fn(cosine_sim, y_train)
            loss.backward()
            optimizer.step()
            optimizer.zero_grad(set_to_none=True) #
            tepoch.set_postfix(train_loss=loss)
            # tepoch.set_postfix(val_loss=loss_sum_val, val_accuracy=100. * acc_val, balanced_val_accuracy=100. * bacc_val)
        loss_sum_val,acc_val, bacc_val = run_validation(model,val_loader,loss_fn, device)
        print('Epoch: %d / %d, ############## the best accuracy in val  %.4f at Epoch: %d  ##############'  % (epoch, 500,100 * best_accuracy,best_epoch))
        # print('Performance in Train: Loss: (%.4f); Accuracy (%.2f)' % (loss_sum, 100 * acc))
        print('Performance in Val: Loss: (%.4f); Accuracy (%.2f)' % (loss_sum_val, 100 * acc_val))
        # checkpoint(model, f"epoch-{epoch}.pth")
        if acc_val > best_accuracy: # compare the performance updates at the val set
            best_accuracy = acc_val
            best_epoch = epoch
            torch.save(model, "best_model.pt")

Epoch 0: 100%|██████████| 1559/1559 [00:18<00:00, 86.10batch/s, train_loss=tensor(0.0859, device='cuda:0', grad_fn=<MseLossBackward0>)]


loss_sum=  0.14722377951284485 ACC=  0.8082978329320244 bacc=  0.6816289213219259 precision=  0.7474619289340102 specificity=  0.9499245093105184 sensitivity=  0.41333333333333333 recall=  0.41333333333333333 MCC=  0.45349833100846737 AUC=  0.8211373047616525 f1=  0.5323090826931767
Epoch: 0 / 500, ############## the best accuracy in val  50.0000 at Epoch: -1  ##############
Performance in Val: Loss: (0.1472); Accuracy (80.83)


Epoch 1: 100%|██████████| 1559/1559 [00:18<00:00, 85.05batch/s, train_loss=tensor(0.1731, device='cuda:0', grad_fn=<MseLossBackward0>)]


loss_sum=  0.13077924714131645 ACC=  0.8292276347471754 bacc=  0.7185773316027866 precision=  0.7867730900798175 specificity=  0.9529441368897836 sensitivity=  0.4842105263157895 recall=  0.4842105263157895 MCC=  0.5223858484798578 AUC=  0.8646406025128245 f1=  0.5994787141615986
Epoch: 1 / 500, ############## the best accuracy in val  80.8298 at Epoch: 0  ##############
Performance in Val: Loss: (0.1308); Accuracy (82.92)


Epoch 2: 100%|██████████| 1559/1559 [00:17<00:00, 87.16batch/s, train_loss=tensor(0.0669, device='cuda:0', grad_fn=<MseLossBackward0>)]


...

loss_sum=  0.055197911689708216 ACC=  0.9375810335247268 bacc=  0.9137128175244351 precision=  0.8965014577259475 specificity=  0.9642677403120282 sensitivity=  0.8631578947368421 recall=  0.8631578947368421 MCC=  0.8376883295643578 AUC=  0.9644119231142779 f1=  0.8795137647479442
Epoch: 497 / 500, ############## the best accuracy in val  94.1285 at Epoch: 207  ##############
Performance in Val: Loss: (0.0552); Accuracy (93.76)


Epoch 498: 100%|██████████| 1559/1559 [00:17<00:00, 88.56batch/s, train_loss=tensor(0.0021, device='cuda:0', grad_fn=<MseLossBackward0>)]


loss_sum=  0.05595234319699939 ACC=  0.9381366919799963 bacc=  0.914315330349023 precision=  0.8978847556528081 specificity=  0.964771011575239 sensitivity=  0.863859649122807 recall=  0.863859649122807 MCC=  0.8391100141345235 AUC=  0.9645238788970414 f1=  0.8805436337625179
Epoch: 498 / 500, ############## the best accuracy in val  94.1285 at Epoch: 207  ##############
Performance in Val: Loss: (0.0560); Accuracy (93.81)


Epoch 499: 100%|██████████| 1559/1559 [00:17<00:00, 87.63batch/s, train_loss=tensor(0.0044, device='cuda:0', grad_fn=<MseLossBackward0>)]


loss_sum=  0.055718712811771584 ACC=  0.937395814039637 bacc=  0.9144872372173514 precision=  0.8935553946415641 specificity=  0.963009562154001 sensitivity=  0.8659649122807017 recall=  0.8659649122807017 MCC=  0.8374535273145642 AUC=  0.9647354294139981 f1=  0.879543834640057
Epoch: 499 / 500, ############## the best accuracy in val  94.1285 at Epoch: 207  ##############
Performance in Val: Loss: (0.0557); Accuracy (93.74)


In [21]:
import torch
# Specify the file path where the entire model is saved
load_path = 'best_model.pt'
# Load the entire model
model_test = torch.load(load_path)
# model_test.to('cuda')
# rename the baseline model
torch.save(model_test, '5500_threshold_best_model_esm2_2560_botlle_neck512_batch_size_16.pt')
run_validation(model_test,test_loader,loss_fn, device) # performance evaluation

loss_sum=  0.06440315387981872 ACC=  0.931640625 bacc=  0.9050261851322859 precision=  0.8871351995235259 specificity=  0.9613344215466232 sensitivity=  0.8487179487179487 recall=  0.8487179487179487 MCC=  0.8218353925747028 AUC=  0.9561684167019812 f1=  0.8675014560279557


(0.06440315387981872, 0.931640625, 0.9050261851322859)

### ESM2 2560 + MolFormer
same bottleneck size, but differnt architecture

#### bottle neck 128

only one neural network layer

In [ ]:
import os
os.chdir('/content/drive/MyDrive/EC_number_kroll/esm2_2560')

In [ ]:
import torch
import torch.nn as nn

class Contrastive_learning_layer(nn.Module):
    def __init__(self):
        super().__init__()
        # self.enzy_refine_layer_1 = nn.Linear(2560, 2560) # W1 and b
        # self.smiles_refine_layer_1 = nn.Linear(768, 768) # W1 and b
        self.enzy_refine_layer_2 = nn.Linear(2560, 128) # W1 and b
        self.smiles_refine_layer_2 = nn.Linear(768, 128) # W1 and b

        self.relu = nn.ReLU()
        # self.batch_norm_enzy = nn.BatchNorm1d(2560)
        # self.batch_norm_smiles = nn.BatchNorm1d(768)
        self.batch_norm_shared = nn.BatchNorm1d(128)

    def forward(self, enzy_embed, smiles_embed):
        # refined_enzy_embed = self.enzy_refine_layer_1(enzy_embed)
        # refined_smiles_embed = self.smiles_refine_layer_1(smiles_embed)

        # refined_enzy_embed = self.batch_norm_enzy(refined_enzy_embed)
        # refined_smiles_embed = self.batch_norm_smiles(refined_smiles_embed)

        refined_enzy_embed = self.relu(enzy_embed)
        refined_smiles_embed = self.relu(smiles_embed)

        refined_enzy_embed = self.enzy_refine_layer_2(refined_enzy_embed)
        refined_smiles_embed = self.smiles_refine_layer_2(refined_smiles_embed)

        refined_enzy_embed = self.batch_norm_shared(refined_enzy_embed)
        refined_smiles_embed = self.batch_norm_shared(refined_smiles_embed)
        refined_enzy_embed = torch.nn.functional.normalize(refined_enzy_embed, dim=1)
        refined_smiles_embed = torch.nn.functional.normalize(refined_smiles_embed, dim=1)

        return refined_enzy_embed, refined_smiles_embed


In [ ]:
def get_ds():
    # Load the saved embeddings_results
    ESP_train_df_enzy = torch.load('ESP_train_df_enzy_esm2_2560.pt')
    ESP_val_df_enzy = torch.load('ESP_val_df_enzy_esm2_2560.pt')
    ESP_test_df_enzy = torch.load('ESP_test_df_enzy_esm2_2560.pt')
    print(ESP_train_df_enzy.shape, ESP_val_df_enzy.shape, ESP_test_df_enzy.shape)
    # Load the saved embeddings_results
    ESP_train_df_smiles = torch.load('ESP_train_df_smiles_esm2_2560.pt')
    ESP_val_df_smiles = torch.load('ESP_val_df_smiles_esm2_2560.pt')
    ESP_test_df_smiles = torch.load('ESP_test_df_smiles_esm2_2560.pt')
    print(ESP_train_df_smiles.shape, ESP_val_df_smiles.shape, ESP_test_df_smiles.shape)

    y_train = torch.load( 'ESP_train_df_label_esm2_2560.pt')
    y_val = torch.load('ESP_val_df_label_esm2_2560.pt')
    y_test = torch.load('ESP_test_df_label_esm2_2560.pt')
    print(y_train.shape,y_val.shape, y_test.shape)
    ESP_train_df_enzy_add = torch.load('ESP_train_df_enzy_>2800_<5500.pt')
    ESP_train_df_smiles_add = torch.load('ESP_train_df_smiles_>2800_<5500.pt')
    y_train_add = torch.load('ESP_train_df_label_>2800_<5500.pt')

    ESP_val_df_enzy_add = torch.load('ESP_val_df_enzy_>2800_<8000.pt')
    ESP_test_df_enzy_add = torch.load('ESP_test_df_enzy_>2800_<8000.pt')
    ESP_val_df_smiles_add = torch.load('ESP_val_df_smiles_>2800_<8000.pt')
    ESP_test_df_smiles_add = torch.load('ESP_test_df_smiles_>2800_<8000.pt')
    y_val_add = torch.load('ESP_val_df_label_>2800_<8000.pt')
    y_test_add = torch.load('ESP_test_df_label_>2800_<8000.pt')
    print(ESP_val_df_enzy_add.shape, ESP_val_df_smiles_add.shape, y_val_add.shape)
    print(ESP_test_df_enzy_add.shape, ESP_test_df_smiles_add.shape, y_test_add.shape)

    ESP_train_df_enzy = torch.cat([ESP_train_df_enzy, ESP_train_df_enzy_add], dim=0)
    ESP_train_df_smiles = torch.cat([ESP_train_df_smiles, ESP_train_df_smiles_add], dim=0)
    y_train = torch.cat([y_train, y_train_add], dim=0)
    print(ESP_train_df_enzy.shape, ESP_train_df_smiles.shape, y_train.shape)

    ESP_val_df_enzy = torch.cat([ESP_val_df_enzy, ESP_val_df_enzy_add], dim=0)
    ESP_val_df_smiles = torch.cat([ESP_val_df_smiles, ESP_val_df_smiles_add], dim=0)
    y_val = torch.cat([y_val, y_val_add], dim=0)
    print(ESP_val_df_enzy.shape, ESP_val_df_smiles.shape, y_val.shape)
    ESP_test_df_enzy = torch.cat([ESP_test_df_enzy, ESP_test_df_enzy_add], dim=0)
    ESP_test_df_smiles = torch.cat([ESP_test_df_smiles, ESP_test_df_smiles_add], dim=0)
    y_test = torch.cat([y_test, y_test_add], dim=0)
    print(ESP_test_df_enzy.shape, ESP_test_df_smiles.shape, y_test.shape)

    train_tensor_dataset = TensorDataset(ESP_train_df_enzy,ESP_train_df_smiles, y_train)
    val_tensor_dataset = TensorDataset(ESP_val_df_enzy,ESP_val_df_smiles, y_val)
    test_tensor_dataset = TensorDataset(ESP_test_df_enzy, ESP_test_df_smiles, y_test)

    # Create TensorDataset and DataLoaders
    batch_size = 16
    train_loader = DataLoader(train_tensor_dataset, batch_size=batch_size, shuffle=True)
    val_loader = DataLoader(val_tensor_dataset, batch_size=batch_size, shuffle=False)
    test_loader = DataLoader(test_tensor_dataset, batch_size=batch_size, shuffle=False)
    print(len(train_loader))
    return train_loader,  val_loader, test_loader

In [ ]:
# design the model, optimizer and loss function
model = Contrastive_learning_layer().to(device)
train_loader,  val_loader, test_loader = get_ds()
optimizer = torch.optim.Adam(model.parameters(),lr= 1e-03)
loss_fn = nn.MSELoss().to(device)

torch.Size([49881, 2560]) torch.Size([5399, 2560]) torch.Size([13312, 2560])
torch.Size([49881, 768]) torch.Size([5399, 768]) torch.Size([13312, 768])
torch.Size([49881, 1]) torch.Size([5399, 1]) torch.Size([13312, 1])
torch.Size([23, 2560]) torch.Size([23, 768]) torch.Size([23, 1])
torch.Size([24, 2560]) torch.Size([24, 768]) torch.Size([24, 1])
torch.Size([50061, 2560]) torch.Size([50061, 768]) torch.Size([50061, 1])
torch.Size([5422, 2560]) torch.Size([5422, 768]) torch.Size([5422, 1])
torch.Size([13336, 2560]) torch.Size([13336, 768]) torch.Size([13336, 1])
3129


In [ ]:
initial_epoch = 0
best_epoch = -1
best_accuracy = 0.5
for epoch in range(initial_epoch, 500):
    torch.cuda.empty_cache()
    model.train()
    with tqdm(train_loader, desc='Processing', unit="batch") as tepoch:
        for ESP_train_df_enzy,ESP_train_df_smiles, y_train in tepoch:
            model.train()
            tepoch.set_description(f"Epoch {epoch}")
            ESP_train_df_enzy = ESP_train_df_enzy.to(device)
            ESP_train_df_smiles = ESP_train_df_smiles.to(device)
            y_train = y_train.squeeze(1).to(device)
            refined_enzy_embed, refined_smiles_embed = model(ESP_train_df_enzy,ESP_train_df_smiles)
            cosine_sim = torch.nn.functional.cosine_similarity(refined_enzy_embed, refined_smiles_embed, dim=1)
            loss = loss_fn(cosine_sim, y_train)
            loss.backward()
            optimizer.step()
            optimizer.zero_grad(set_to_none=True) #
            tepoch.set_postfix(train_loss=loss)
            # tepoch.set_postfix(val_loss=loss_sum_val, val_accuracy=100. * acc_val, balanced_val_accuracy=100. * bacc_val)
        loss_sum_val,acc_val, bacc_val = run_validation(model,val_loader,loss_fn, device)
        print('Epoch: %d / %d, ############## the best accuracy in val  %.4f at Epoch: %d  ##############'  % (epoch, 500,100 * best_accuracy,best_epoch))
        # print('Performance in Train: Loss: (%.4f); Accuracy (%.2f)' % (loss_sum, 100 * acc))
        print('Performance in Val: Loss: (%.4f); Accuracy (%.2f)' % (loss_sum_val, 100 * acc_val))
        # checkpoint(model, f"epoch-{epoch}.pth")
        if acc_val > best_accuracy: # compare the performance updates at the val set
            best_accuracy = acc_val
            best_epoch = epoch
            torch.save(model, "best_model.pt")

In [ ]:
import torch
# Specify the file path where the entire model is saved
load_path = 'best_model.pt'
# Load the entire model
model_test = torch.load(load_path)
# model_test.to('cuda')
# rename the baseline model
torch.save(model_test, '5500_threshold_best_model_esm2_2560_botlle_neck128_batch_16_only_one_bottleneck_layer.pt')
run_validation(model_test,test_loader,loss_fn, device) # performance evaluation

loss_sum=  0.39505495987073197 ACC=  0.7363527294541091 bacc=  0.5 precision=  nan specificity=  1.0 sensitivity=  0.0 recall=  0.0 MCC=  nan AUC=  0.669399402556599 f1=  nan


<ipython-input-3-c7858174dfc2>:33: RuntimeWarning: invalid value encountered in scalar divide
  precision = tp/(tp+fp)
<ipython-input-3-c7858174dfc2>:35: RuntimeWarning: invalid value encountered in scalar divide
  MCC = (tp*tn-fp*fn)/np.sqrt((tp+fp)*(tp+fn)*(tn+fp)*(tn+fn))


(0.39505495987073197, 0.7363527294541091, 0.5)

#### bottle neck 128

no relu activation ---- additional test

In [10]:
import os
os.chdir('/content/drive/MyDrive/EC_number_kroll/esm2_2560')

In [11]:
import torch
import torch.nn as nn

class Contrastive_learning_layer(nn.Module):
    def __init__(self):
        super().__init__()
        self.enzy_refine_layer_1 = nn.Linear(2560, 2560) # W1 and b
        self.smiles_refine_layer_1 = nn.Linear(768, 768) # W1 and b
        self.enzy_refine_layer_2 = nn.Linear(2560, 128) # W1 and b
        self.smiles_refine_layer_2 = nn.Linear(768, 128) # W1 and b

        self.relu = nn.ReLU()
        self.batch_norm_enzy = nn.BatchNorm1d(2560)
        self.batch_norm_smiles = nn.BatchNorm1d(768)
        self.batch_norm_shared = nn.BatchNorm1d(128)

    def forward(self, enzy_embed, smiles_embed):
        refined_enzy_embed = self.enzy_refine_layer_1(enzy_embed)
        refined_smiles_embed = self.smiles_refine_layer_1(smiles_embed)

        refined_enzy_embed = self.batch_norm_enzy(refined_enzy_embed)
        refined_smiles_embed = self.batch_norm_smiles(refined_smiles_embed)

        # refined_enzy_embed = self.relu(refined_enzy_embed)
        # refined_smiles_embed = self.relu(refined_smiles_embed)

        refined_enzy_embed = self.enzy_refine_layer_2(refined_enzy_embed)
        refined_smiles_embed = self.smiles_refine_layer_2(refined_smiles_embed)

        refined_enzy_embed = self.batch_norm_shared(refined_enzy_embed)
        refined_smiles_embed = self.batch_norm_shared(refined_smiles_embed)
        refined_enzy_embed = torch.nn.functional.normalize(refined_enzy_embed, dim=1)
        refined_smiles_embed = torch.nn.functional.normalize(refined_smiles_embed, dim=1)

        return refined_enzy_embed, refined_smiles_embed


In [12]:
def get_ds():
    # Load the saved embeddings_results
    ESP_train_df_enzy = torch.load('ESP_train_df_enzy_esm2_2560.pt')
    ESP_val_df_enzy = torch.load('ESP_val_df_enzy_esm2_2560.pt')
    ESP_test_df_enzy = torch.load('ESP_test_df_enzy_esm2_2560.pt')
    print(ESP_train_df_enzy.shape, ESP_val_df_enzy.shape, ESP_test_df_enzy.shape)
    # Load the saved embeddings_results
    ESP_train_df_smiles = torch.load('ESP_train_df_smiles_esm2_2560.pt')
    ESP_val_df_smiles = torch.load('ESP_val_df_smiles_esm2_2560.pt')
    ESP_test_df_smiles = torch.load('ESP_test_df_smiles_esm2_2560.pt')
    print(ESP_train_df_smiles.shape, ESP_val_df_smiles.shape, ESP_test_df_smiles.shape)

    y_train = torch.load( 'ESP_train_df_label_esm2_2560.pt')
    y_val = torch.load('ESP_val_df_label_esm2_2560.pt')
    y_test = torch.load('ESP_test_df_label_esm2_2560.pt')
    print(y_train.shape,y_val.shape, y_test.shape)
    ESP_train_df_enzy_add = torch.load('ESP_train_df_enzy_>2800_<5500.pt')
    ESP_train_df_smiles_add = torch.load('ESP_train_df_smiles_>2800_<5500.pt')
    y_train_add = torch.load('ESP_train_df_label_>2800_<5500.pt')

    ESP_val_df_enzy_add = torch.load('ESP_val_df_enzy_>2800_<8000.pt')
    ESP_test_df_enzy_add = torch.load('ESP_test_df_enzy_>2800_<8000.pt')
    ESP_val_df_smiles_add = torch.load('ESP_val_df_smiles_>2800_<8000.pt')
    ESP_test_df_smiles_add = torch.load('ESP_test_df_smiles_>2800_<8000.pt')
    y_val_add = torch.load('ESP_val_df_label_>2800_<8000.pt')
    y_test_add = torch.load('ESP_test_df_label_>2800_<8000.pt')
    print(ESP_val_df_enzy_add.shape, ESP_val_df_smiles_add.shape, y_val_add.shape)
    print(ESP_test_df_enzy_add.shape, ESP_test_df_smiles_add.shape, y_test_add.shape)

    ESP_train_df_enzy = torch.cat([ESP_train_df_enzy, ESP_train_df_enzy_add], dim=0)
    ESP_train_df_smiles = torch.cat([ESP_train_df_smiles, ESP_train_df_smiles_add], dim=0)
    y_train = torch.cat([y_train, y_train_add], dim=0)
    print(ESP_train_df_enzy.shape, ESP_train_df_smiles.shape, y_train.shape)

    ESP_val_df_enzy = torch.cat([ESP_val_df_enzy, ESP_val_df_enzy_add], dim=0)
    ESP_val_df_smiles = torch.cat([ESP_val_df_smiles, ESP_val_df_smiles_add], dim=0)
    y_val = torch.cat([y_val, y_val_add], dim=0)
    print(ESP_val_df_enzy.shape, ESP_val_df_smiles.shape, y_val.shape)
    ESP_test_df_enzy = torch.cat([ESP_test_df_enzy, ESP_test_df_enzy_add], dim=0)
    ESP_test_df_smiles = torch.cat([ESP_test_df_smiles, ESP_test_df_smiles_add], dim=0)
    y_test = torch.cat([y_test, y_test_add], dim=0)
    print(ESP_test_df_enzy.shape, ESP_test_df_smiles.shape, y_test.shape)

    train_tensor_dataset = TensorDataset(ESP_train_df_enzy,ESP_train_df_smiles, y_train)
    val_tensor_dataset = TensorDataset(ESP_val_df_enzy,ESP_val_df_smiles, y_val)
    test_tensor_dataset = TensorDataset(ESP_test_df_enzy, ESP_test_df_smiles, y_test)

    # Create TensorDataset and DataLoaders
    batch_size = 16
    train_loader = DataLoader(train_tensor_dataset, batch_size=batch_size, shuffle=True)
    val_loader = DataLoader(val_tensor_dataset, batch_size=batch_size, shuffle=False)
    test_loader = DataLoader(test_tensor_dataset, batch_size=batch_size, shuffle=False)
    print(len(train_loader))
    return train_loader,  val_loader, test_loader

In [13]:
# design the model, optimizer and loss function
model = Contrastive_learning_layer().to(device)
train_loader,  val_loader, test_loader = get_ds()
optimizer = torch.optim.Adam(model.parameters(),lr= 1e-03)
loss_fn = nn.MSELoss().to(device)

torch.Size([49881, 2560]) torch.Size([5399, 2560]) torch.Size([13312, 2560])
torch.Size([49881, 768]) torch.Size([5399, 768]) torch.Size([13312, 768])
torch.Size([49881, 1]) torch.Size([5399, 1]) torch.Size([13312, 1])
torch.Size([23, 2560]) torch.Size([23, 768]) torch.Size([23, 1])
torch.Size([24, 2560]) torch.Size([24, 768]) torch.Size([24, 1])
torch.Size([50061, 2560]) torch.Size([50061, 768]) torch.Size([50061, 1])
torch.Size([5422, 2560]) torch.Size([5422, 768]) torch.Size([5422, 1])
torch.Size([13336, 2560]) torch.Size([13336, 768]) torch.Size([13336, 1])
3129


In [14]:
initial_epoch = 0
best_epoch = -1
best_accuracy = 0.5
for epoch in range(initial_epoch, 500):
    torch.cuda.empty_cache()
    model.train()
    with tqdm(train_loader, desc='Processing', unit="batch") as tepoch:
        for ESP_train_df_enzy,ESP_train_df_smiles, y_train in tepoch:
            model.train()
            tepoch.set_description(f"Epoch {epoch}")
            ESP_train_df_enzy = ESP_train_df_enzy.to(device)
            ESP_train_df_smiles = ESP_train_df_smiles.to(device)
            y_train = y_train.squeeze(1).to(device)
            refined_enzy_embed, refined_smiles_embed = model(ESP_train_df_enzy,ESP_train_df_smiles)
            cosine_sim = torch.nn.functional.cosine_similarity(refined_enzy_embed, refined_smiles_embed, dim=1)
            loss = loss_fn(cosine_sim, y_train)
            loss.backward()
            optimizer.step()
            optimizer.zero_grad(set_to_none=True) #
            tepoch.set_postfix(train_loss=loss)
            # tepoch.set_postfix(val_loss=loss_sum_val, val_accuracy=100. * acc_val, balanced_val_accuracy=100. * bacc_val)
        loss_sum_val,acc_val, bacc_val = run_validation(model,val_loader,loss_fn, device)
        print('Epoch: %d / %d, ############## the best accuracy in val  %.4f at Epoch: %d  ##############'  % (epoch, 500,100 * best_accuracy,best_epoch))
        # print('Performance in Train: Loss: (%.4f); Accuracy (%.2f)' % (loss_sum, 100 * acc))
        print('Performance in Val: Loss: (%.4f); Accuracy (%.2f)' % (loss_sum_val, 100 * acc_val))
        # checkpoint(model, f"epoch-{epoch}.pth")
        if acc_val > best_accuracy: # compare the performance updates at the val set
            best_accuracy = acc_val
            best_epoch = epoch
            torch.save(model, "best_model.pt")

Epoch 0: 100%|██████████| 3129/3129 [00:32<00:00, 97.71batch/s, train_loss=tensor(0.1273, device='cuda:0', grad_fn=<MseLossBackward0>)]


loss_sum=  0.14751488151122158 ACC=  0.8085577277757285 bacc=  0.7047779236335564 precision=  0.6974874371859296 specificity=  0.9245803056877976 sensitivity=  0.48497554157931516 recall=  0.48497554157931516 MCC=  0.46634519911065175 AUC=  0.835596023967974 f1=  0.5721352019785656
Epoch: 0 / 500, ############## the best accuracy in val  50.0000 at Epoch: -1  ##############
Performance in Val: Loss: (0.1475); Accuracy (80.86)


Epoch 1: 100%|██████████| 3129/3129 [00:33<00:00, 94.80batch/s, train_loss=tensor(0.2161, device='cuda:0', grad_fn=<MseLossBackward0>)]


loss_sum=  0.13403267989204345 ACC=  0.8212836591663593 bacc=  0.7174566079058735 precision=  0.7401247401247402 specificity=  0.9373590578802306 sensitivity=  0.4975541579315164 recall=  0.4975541579315164 MCC=  0.5017741920030175 AUC=  0.8650285119156116 f1=  0.5950689511073967
Epoch: 1 / 500, ############## the best accuracy in val  80.8558 at Epoch: 0  ##############
Performance in Val: Loss: (0.1340); Accuracy (82.13)


Epoch 2: 100%|██████████| 3129/3129 [00:33<00:00, 92.80batch/s, train_loss=tensor(0.1687, device='cuda:0', grad_fn=<MseLossBackward0>)]


...

loss_sum=  0.07095977083771629 ACC=  0.9348948727406861 bacc=  0.9010892082307485 precision=  0.9158950617283951 specificity=  0.9726885492357805 sensitivity=  0.8294898672257163 recall=  0.8294898672257163 MCC=  0.8290191082029881 AUC=  0.9556285009545412 f1=  0.8705537220388705
Epoch: 497 / 500, ############## the best accuracy in val  93.6924 at Epoch: 444  ##############
Performance in Val: Loss: (0.0710); Accuracy (93.49)


Epoch 498: 100%|██████████| 3129/3129 [00:33<00:00, 92.06batch/s, train_loss=tensor(0.0289, device='cuda:0', grad_fn=<MseLossBackward0>)]


loss_sum=  0.07287940341199042 ACC=  0.9358170416820362 bacc=  0.9035086106562967 precision=  0.9143075745983168 specificity=  0.9719368579303432 sensitivity=  0.8350803633822502 recall=  0.8350803633822502 MCC=  0.8316120424117547 AUC=  0.9542712367677029 f1=  0.872899926953981
Epoch: 498 / 500, ############## the best accuracy in val  93.6924 at Epoch: 444  ##############
Performance in Val: Loss: (0.0729); Accuracy (93.58)


Epoch 499: 100%|██████████| 3129/3129 [00:33<00:00, 93.71batch/s, train_loss=tensor(0.0192, device='cuda:0', grad_fn=<MseLossBackward0>)]


loss_sum=  0.07051255676626147 ACC=  0.9367392106233862 bacc=  0.9027902753242314 precision=  0.9217054263565891 specificity=  0.9746930593836132 sensitivity=  0.8308874912648497 recall=  0.8308874912648497 MCC=  0.8338628804634474 AUC=  0.9562345991268614 f1=  0.8739434031606028
Epoch: 499 / 500, ############## the best accuracy in val  93.6924 at Epoch: 444  ##############
Performance in Val: Loss: (0.0705); Accuracy (93.67)


In [15]:
import torch
# Specify the file path where the entire model is saved
load_path = 'best_model.pt'
# Load the entire model
model_test = torch.load(load_path)
# model_test.to('cuda')
# rename the baseline model
torch.save(model_test, '5500_threshold_best_model_esm2_2560_botlle_neck128_batch_16_no_relu_additional_test.pt')
run_validation(model_test,test_loader,loss_fn, device) # performance evaluation

loss_sum=  0.08043941494459353 ACC=  0.9220905818836233 bacc=  0.8779908083848291 precision=  0.9072673462676751 specificity=  0.9712830957230143 sensitivity=  0.784698521046644 recall=  0.784698521046644 MCC=  0.7939077224757125 AUC=  0.9399998175347379 f1=  0.8415433887448528


(0.08043941494459353, 0.9220905818836233, 0.8779908083848291)

#### bottle neck 128

only one neural network layer  change relu lcoation


In [ ]:
import os
os.chdir('/content/drive/MyDrive/EC_number_kroll/esm2_2560')

In [ ]:
import torch
import torch.nn as nn

class Contrastive_learning_layer(nn.Module):
    def __init__(self):
        super().__init__()
        # self.enzy_refine_layer_1 = nn.Linear(2560, 2560) # W1 and b
        # self.smiles_refine_layer_1 = nn.Linear(768, 768) # W1 and b
        self.enzy_refine_layer_2 = nn.Linear(2560, 128) # W1 and b
        self.smiles_refine_layer_2 = nn.Linear(768, 128) # W1 and b

        self.relu = nn.ReLU()
        # self.batch_norm_enzy = nn.BatchNorm1d(2560)
        # self.batch_norm_smiles = nn.BatchNorm1d(768)
        self.batch_norm_shared = nn.BatchNorm1d(128)

    def forward(self, enzy_embed, smiles_embed):
        # refined_enzy_embed = self.enzy_refine_layer_1(enzy_embed)
        # refined_smiles_embed = self.smiles_refine_layer_1(smiles_embed)

        # refined_enzy_embed = self.batch_norm_enzy(refined_enzy_embed)
        # refined_smiles_embed = self.batch_norm_smiles(refined_smiles_embed)


        refined_enzy_embed = self.enzy_refine_layer_2(enzy_embed)
        refined_smiles_embed = self.smiles_refine_layer_2(smiles_embed)

        refined_enzy_embed = self.relu(refined_enzy_embed)
        refined_smiles_embed = self.relu(refined_smiles_embed)

        refined_enzy_embed = self.batch_norm_shared(refined_enzy_embed)
        refined_smiles_embed = self.batch_norm_shared(refined_smiles_embed)
        refined_enzy_embed = torch.nn.functional.normalize(refined_enzy_embed, dim=1)
        refined_smiles_embed = torch.nn.functional.normalize(refined_smiles_embed, dim=1)

        return refined_enzy_embed, refined_smiles_embed


In [ ]:
def get_ds():
    # Load the saved embeddings_results
    ESP_train_df_enzy = torch.load('ESP_train_df_enzy_esm2_2560.pt')
    ESP_val_df_enzy = torch.load('ESP_val_df_enzy_esm2_2560.pt')
    ESP_test_df_enzy = torch.load('ESP_test_df_enzy_esm2_2560.pt')
    print(ESP_train_df_enzy.shape, ESP_val_df_enzy.shape, ESP_test_df_enzy.shape)
    # Load the saved embeddings_results
    ESP_train_df_smiles = torch.load('ESP_train_df_smiles_esm2_2560.pt')
    ESP_val_df_smiles = torch.load('ESP_val_df_smiles_esm2_2560.pt')
    ESP_test_df_smiles = torch.load('ESP_test_df_smiles_esm2_2560.pt')
    print(ESP_train_df_smiles.shape, ESP_val_df_smiles.shape, ESP_test_df_smiles.shape)

    y_train = torch.load( 'ESP_train_df_label_esm2_2560.pt')
    y_val = torch.load('ESP_val_df_label_esm2_2560.pt')
    y_test = torch.load('ESP_test_df_label_esm2_2560.pt')
    print(y_train.shape,y_val.shape, y_test.shape)
    ESP_train_df_enzy_add = torch.load('ESP_train_df_enzy_>2800_<5500.pt')
    ESP_train_df_smiles_add = torch.load('ESP_train_df_smiles_>2800_<5500.pt')
    y_train_add = torch.load('ESP_train_df_label_>2800_<5500.pt')

    ESP_val_df_enzy_add = torch.load('ESP_val_df_enzy_>2800_<8000.pt')
    ESP_test_df_enzy_add = torch.load('ESP_test_df_enzy_>2800_<8000.pt')
    ESP_val_df_smiles_add = torch.load('ESP_val_df_smiles_>2800_<8000.pt')
    ESP_test_df_smiles_add = torch.load('ESP_test_df_smiles_>2800_<8000.pt')
    y_val_add = torch.load('ESP_val_df_label_>2800_<8000.pt')
    y_test_add = torch.load('ESP_test_df_label_>2800_<8000.pt')
    print(ESP_val_df_enzy_add.shape, ESP_val_df_smiles_add.shape, y_val_add.shape)
    print(ESP_test_df_enzy_add.shape, ESP_test_df_smiles_add.shape, y_test_add.shape)

    ESP_train_df_enzy = torch.cat([ESP_train_df_enzy, ESP_train_df_enzy_add], dim=0)
    ESP_train_df_smiles = torch.cat([ESP_train_df_smiles, ESP_train_df_smiles_add], dim=0)
    y_train = torch.cat([y_train, y_train_add], dim=0)
    print(ESP_train_df_enzy.shape, ESP_train_df_smiles.shape, y_train.shape)

    ESP_val_df_enzy = torch.cat([ESP_val_df_enzy, ESP_val_df_enzy_add], dim=0)
    ESP_val_df_smiles = torch.cat([ESP_val_df_smiles, ESP_val_df_smiles_add], dim=0)
    y_val = torch.cat([y_val, y_val_add], dim=0)
    print(ESP_val_df_enzy.shape, ESP_val_df_smiles.shape, y_val.shape)
    ESP_test_df_enzy = torch.cat([ESP_test_df_enzy, ESP_test_df_enzy_add], dim=0)
    ESP_test_df_smiles = torch.cat([ESP_test_df_smiles, ESP_test_df_smiles_add], dim=0)
    y_test = torch.cat([y_test, y_test_add], dim=0)
    print(ESP_test_df_enzy.shape, ESP_test_df_smiles.shape, y_test.shape)

    train_tensor_dataset = TensorDataset(ESP_train_df_enzy,ESP_train_df_smiles, y_train)
    val_tensor_dataset = TensorDataset(ESP_val_df_enzy,ESP_val_df_smiles, y_val)
    test_tensor_dataset = TensorDataset(ESP_test_df_enzy, ESP_test_df_smiles, y_test)

    # Create TensorDataset and DataLoaders
    batch_size = 16
    train_loader = DataLoader(train_tensor_dataset, batch_size=batch_size, shuffle=True)
    val_loader = DataLoader(val_tensor_dataset, batch_size=batch_size, shuffle=False)
    test_loader = DataLoader(test_tensor_dataset, batch_size=batch_size, shuffle=False)
    print(len(train_loader))
    return train_loader,  val_loader, test_loader

In [ ]:
# design the model, optimizer and loss function
model = Contrastive_learning_layer().to(device)
train_loader,  val_loader, test_loader = get_ds()
optimizer = torch.optim.Adam(model.parameters(),lr= 1e-03)
loss_fn = nn.MSELoss().to(device)

torch.Size([49881, 2560]) torch.Size([5399, 2560]) torch.Size([13312, 2560])
torch.Size([49881, 768]) torch.Size([5399, 768]) torch.Size([13312, 768])
torch.Size([49881, 1]) torch.Size([5399, 1]) torch.Size([13312, 1])
torch.Size([23, 2560]) torch.Size([23, 768]) torch.Size([23, 1])
torch.Size([24, 2560]) torch.Size([24, 768]) torch.Size([24, 1])
torch.Size([50061, 2560]) torch.Size([50061, 768]) torch.Size([50061, 1])
torch.Size([5422, 2560]) torch.Size([5422, 768]) torch.Size([5422, 1])
torch.Size([13336, 2560]) torch.Size([13336, 768]) torch.Size([13336, 1])
3129


In [ ]:
initial_epoch = 0
best_epoch = -1
best_accuracy = 0.5
for epoch in range(initial_epoch, 500):
    torch.cuda.empty_cache()
    model.train()
    with tqdm(train_loader, desc='Processing', unit="batch") as tepoch:
        for ESP_train_df_enzy,ESP_train_df_smiles, y_train in tepoch:
            model.train()
            tepoch.set_description(f"Epoch {epoch}")
            ESP_train_df_enzy = ESP_train_df_enzy.to(device)
            ESP_train_df_smiles = ESP_train_df_smiles.to(device)
            y_train = y_train.squeeze(1).to(device)
            refined_enzy_embed, refined_smiles_embed = model(ESP_train_df_enzy,ESP_train_df_smiles)
            cosine_sim = torch.nn.functional.cosine_similarity(refined_enzy_embed, refined_smiles_embed, dim=1)
            loss = loss_fn(cosine_sim, y_train)
            loss.backward()
            optimizer.step()
            optimizer.zero_grad(set_to_none=True) #
            tepoch.set_postfix(train_loss=loss)
            # tepoch.set_postfix(val_loss=loss_sum_val, val_accuracy=100. * acc_val, balanced_val_accuracy=100. * bacc_val)
        loss_sum_val,acc_val, bacc_val = run_validation(model,val_loader,loss_fn, device)
        print('Epoch: %d / %d, ############## the best accuracy in val  %.4f at Epoch: %d  ##############'  % (epoch, 500,100 * best_accuracy,best_epoch))
        # print('Performance in Train: Loss: (%.4f); Accuracy (%.2f)' % (loss_sum, 100 * acc))
        print('Performance in Val: Loss: (%.4f); Accuracy (%.2f)' % (loss_sum_val, 100 * acc_val))
        # checkpoint(model, f"epoch-{epoch}.pth")
        if acc_val > best_accuracy: # compare the performance updates at the val set
            best_accuracy = acc_val
            best_epoch = epoch
            torch.save(model, "best_model.pt")

Epoch 0: 100%|██████████| 3129/3129 [00:23<00:00, 130.75batch/s, train_loss=tensor(0.1656, device='cuda:0', grad_fn=<MseLossBackward0>)]
<ipython-input-3-c7858174dfc2>:33: RuntimeWarning: invalid value encountered in scalar divide
  precision = tp/(tp+fp)
<ipython-input-3-c7858174dfc2>:35: RuntimeWarning: invalid value encountered in scalar divide
  MCC = (tp*tn-fp*fn)/np.sqrt((tp+fp)*(tp+fn)*(tn+fp)*(tn+fn))


loss_sum=  0.9455089756784889 ACC=  0.7360752489856142 bacc=  0.5 precision=  nan specificity=  1.0 sensitivity=  0.0 recall=  0.0 MCC=  nan AUC=  0.5693841016500963 f1=  nan
Epoch: 0 / 500, ############## the best accuracy in val  50.0000 at Epoch: -1  ##############
Performance in Val: Loss: (0.9455); Accuracy (73.61)


Epoch 1: 100%|██████████| 3129/3129 [00:23<00:00, 131.47batch/s, train_loss=tensor(0.0912, device='cuda:0', grad_fn=<MseLossBackward0>)]
<ipython-input-3-c7858174dfc2>:33: RuntimeWarning: invalid value encountered in scalar divide
  precision = tp/(tp+fp)
<ipython-input-3-c7858174dfc2>:35: RuntimeWarning: invalid value encountered in scalar divide
  MCC = (tp*tn-fp*fn)/np.sqrt((tp+fp)*(tp+fn)*(tn+fp)*(tn+fn))


loss_sum=  0.7677338993215279 ACC=  0.7360752489856142 bacc=  0.5 precision=  nan specificity=  1.0 sensitivity=  0.0 recall=  0.0 MCC=  nan AUC=  0.6363763786479048 f1=  nan
Epoch: 1 / 500, ############## the best accuracy in val  73.6075 at Epoch: 0  ##############
Performance in Val: Loss: (0.7677); Accuracy (73.61)


Epoch 2: 100%|██████████| 3129/3129 [00:24<00:00, 127.28batch/s, train_loss=tensor(0.1304, device='cuda:0', grad_fn=<MseLossBackward0>)]
<ipython-input-3-c7858174dfc2>:33: RuntimeWarning: invalid value encountered in scalar divide
  precision = tp/(tp+fp)
<ipython-input-3-c7858174dfc2>:35: RuntimeWarning: invalid value encountered in scalar divide
  MCC = (tp*tn-fp*fn)/np.sqrt((tp+fp)*(tp+fn)*(tn+fp)*(tn+fn))


...

loss_sum=  0.23794739743403454 ACC=  0.7414238288454444 bacc=  0.5134946361668751 precision=  0.7457627118644068 specificity=  0.9962415434728138 sensitivity=  0.030747728860936407 recall=  0.030747728860936407 MCC=  0.11466264402785399 AUC=  0.8731768246549145 f1=  0.059060402684563765
Epoch: 497 / 500, ############## the best accuracy in val  74.8432 at Epoch: 89  ##############
Performance in Val: Loss: (0.2379); Accuracy (74.14)


Epoch 498: 100%|██████████| 3129/3129 [00:27<00:00, 114.56batch/s, train_loss=tensor(0.0463, device='cuda:0', grad_fn=<MseLossBackward0>)]


loss_sum=  0.2463154994764511 ACC=  0.7406860936923645 bacc=  0.511648763876654 precision=  0.7450980392156863 specificity=  0.996742671009772 sensitivity=  0.026554856743535988 recall=  0.026554856743535988 MCC=  0.10637947784647746 AUC=  0.8714472167548193 f1=  0.05128205128205128
Epoch: 498 / 500, ############## the best accuracy in val  74.8432 at Epoch: 89  ##############
Performance in Val: Loss: (0.2463); Accuracy (74.07)


Epoch 499: 100%|██████████| 3129/3129 [00:27<00:00, 115.39batch/s, train_loss=tensor(0.0373, device='cuda:0', grad_fn=<MseLossBackward0>)]


loss_sum=  0.23704575900548855 ACC=  0.7427148653633345 bacc=  0.5141474852310081 precision=  0.86 specificity=  0.9982460536206464 sensitivity=  0.03004891684136967 recall=  0.03004891684136967 MCC=  0.13047188036725474 AUC=  0.876087811832388 f1=  0.05806887238352464
Epoch: 499 / 500, ############## the best accuracy in val  74.8432 at Epoch: 89  ##############
Performance in Val: Loss: (0.2370); Accuracy (74.27)


In [ ]:
import torch
# Specify the file path where the entire model is saved
load_path = 'best_model.pt'
# Load the entire model
model_test = torch.load(load_path)
# model_test.to('cuda')
# rename the baseline model
torch.save(model_test, '5500_threshold_best_model_esm2_2560_botlle_neck128_batch_16_only_one_bottleneck_layer.pt')
run_validation(model_test,test_loader,loss_fn, device) # performance evaluation

loss_sum=  0.24135563117664138 ACC=  0.7431763647270546 bacc=  0.5198789241616445 precision=  0.6872427983539094 specificity=  0.9922606924643584 sensitivity=  0.0474971558589306 recall=  0.0474971558589306 MCC=  0.13097256378351874 AUC=  0.8416281896665578 f1=  0.088853418462357


(0.24135563117664138, 0.7431763647270546, 0.5198789241616445)

#### bottle neck 128

no relu activation

In [ ]:
import os
os.chdir('/content/drive/MyDrive/EC_number_kroll/esm2_2560')

In [ ]:
import torch
import torch.nn as nn

class Contrastive_learning_layer(nn.Module):
    def __init__(self):
        super().__init__()
        self.enzy_refine_layer_1 = nn.Linear(2560, 2560) # W1 and b
        self.smiles_refine_layer_1 = nn.Linear(768, 768) # W1 and b
        self.enzy_refine_layer_2 = nn.Linear(2560, 128) # W1 and b
        self.smiles_refine_layer_2 = nn.Linear(768, 128) # W1 and b

        self.relu = nn.ReLU()
        self.batch_norm_enzy = nn.BatchNorm1d(2560)
        self.batch_norm_smiles = nn.BatchNorm1d(768)
        self.batch_norm_shared = nn.BatchNorm1d(128)

    def forward(self, enzy_embed, smiles_embed):
        refined_enzy_embed = self.enzy_refine_layer_1(enzy_embed)
        refined_smiles_embed = self.smiles_refine_layer_1(smiles_embed)

        refined_enzy_embed = self.batch_norm_enzy(refined_enzy_embed)
        refined_smiles_embed = self.batch_norm_smiles(refined_smiles_embed)

        # refined_enzy_embed = self.relu(refined_enzy_embed)
        # refined_smiles_embed = self.relu(refined_smiles_embed)

        refined_enzy_embed = self.enzy_refine_layer_2(refined_enzy_embed)
        refined_smiles_embed = self.smiles_refine_layer_2(refined_smiles_embed)

        refined_enzy_embed = self.batch_norm_shared(refined_enzy_embed)
        refined_smiles_embed = self.batch_norm_shared(refined_smiles_embed)
        refined_enzy_embed = torch.nn.functional.normalize(refined_enzy_embed, dim=1)
        refined_smiles_embed = torch.nn.functional.normalize(refined_smiles_embed, dim=1)

        return refined_enzy_embed, refined_smiles_embed


In [ ]:
def get_ds():
    # Load the saved embeddings_results
    ESP_train_df_enzy = torch.load('ESP_train_df_enzy_esm2_2560.pt')
    ESP_val_df_enzy = torch.load('ESP_val_df_enzy_esm2_2560.pt')
    ESP_test_df_enzy = torch.load('ESP_test_df_enzy_esm2_2560.pt')
    print(ESP_train_df_enzy.shape, ESP_val_df_enzy.shape, ESP_test_df_enzy.shape)
    # Load the saved embeddings_results
    ESP_train_df_smiles = torch.load('ESP_train_df_smiles_esm2_2560.pt')
    ESP_val_df_smiles = torch.load('ESP_val_df_smiles_esm2_2560.pt')
    ESP_test_df_smiles = torch.load('ESP_test_df_smiles_esm2_2560.pt')
    print(ESP_train_df_smiles.shape, ESP_val_df_smiles.shape, ESP_test_df_smiles.shape)

    y_train = torch.load( 'ESP_train_df_label_esm2_2560.pt')
    y_val = torch.load('ESP_val_df_label_esm2_2560.pt')
    y_test = torch.load('ESP_test_df_label_esm2_2560.pt')
    print(y_train.shape,y_val.shape, y_test.shape)
    ESP_train_df_enzy_add = torch.load('ESP_train_df_enzy_>2800_<5500.pt')
    ESP_train_df_smiles_add = torch.load('ESP_train_df_smiles_>2800_<5500.pt')
    y_train_add = torch.load('ESP_train_df_label_>2800_<5500.pt')

    ESP_val_df_enzy_add = torch.load('ESP_val_df_enzy_>2800_<8000.pt')
    ESP_test_df_enzy_add = torch.load('ESP_test_df_enzy_>2800_<8000.pt')
    ESP_val_df_smiles_add = torch.load('ESP_val_df_smiles_>2800_<8000.pt')
    ESP_test_df_smiles_add = torch.load('ESP_test_df_smiles_>2800_<8000.pt')
    y_val_add = torch.load('ESP_val_df_label_>2800_<8000.pt')
    y_test_add = torch.load('ESP_test_df_label_>2800_<8000.pt')
    print(ESP_val_df_enzy_add.shape, ESP_val_df_smiles_add.shape, y_val_add.shape)
    print(ESP_test_df_enzy_add.shape, ESP_test_df_smiles_add.shape, y_test_add.shape)

    ESP_train_df_enzy = torch.cat([ESP_train_df_enzy, ESP_train_df_enzy_add], dim=0)
    ESP_train_df_smiles = torch.cat([ESP_train_df_smiles, ESP_train_df_smiles_add], dim=0)
    y_train = torch.cat([y_train, y_train_add], dim=0)
    print(ESP_train_df_enzy.shape, ESP_train_df_smiles.shape, y_train.shape)

    ESP_val_df_enzy = torch.cat([ESP_val_df_enzy, ESP_val_df_enzy_add], dim=0)
    ESP_val_df_smiles = torch.cat([ESP_val_df_smiles, ESP_val_df_smiles_add], dim=0)
    y_val = torch.cat([y_val, y_val_add], dim=0)
    print(ESP_val_df_enzy.shape, ESP_val_df_smiles.shape, y_val.shape)
    ESP_test_df_enzy = torch.cat([ESP_test_df_enzy, ESP_test_df_enzy_add], dim=0)
    ESP_test_df_smiles = torch.cat([ESP_test_df_smiles, ESP_test_df_smiles_add], dim=0)
    y_test = torch.cat([y_test, y_test_add], dim=0)
    print(ESP_test_df_enzy.shape, ESP_test_df_smiles.shape, y_test.shape)

    train_tensor_dataset = TensorDataset(ESP_train_df_enzy,ESP_train_df_smiles, y_train)
    val_tensor_dataset = TensorDataset(ESP_val_df_enzy,ESP_val_df_smiles, y_val)
    test_tensor_dataset = TensorDataset(ESP_test_df_enzy, ESP_test_df_smiles, y_test)

    # Create TensorDataset and DataLoaders
    batch_size = 16
    train_loader = DataLoader(train_tensor_dataset, batch_size=batch_size, shuffle=True)
    val_loader = DataLoader(val_tensor_dataset, batch_size=batch_size, shuffle=False)
    test_loader = DataLoader(test_tensor_dataset, batch_size=batch_size, shuffle=False)
    print(len(train_loader))
    return train_loader,  val_loader, test_loader

In [ ]:
# design the model, optimizer and loss function
model = Contrastive_learning_layer().to(device)
train_loader,  val_loader, test_loader = get_ds()
optimizer = torch.optim.Adam(model.parameters(),lr= 1e-03)
loss_fn = nn.MSELoss().to(device)

torch.Size([49881, 2560]) torch.Size([5399, 2560]) torch.Size([13312, 2560])
torch.Size([49881, 768]) torch.Size([5399, 768]) torch.Size([13312, 768])
torch.Size([49881, 1]) torch.Size([5399, 1]) torch.Size([13312, 1])
torch.Size([23, 2560]) torch.Size([23, 768]) torch.Size([23, 1])
torch.Size([24, 2560]) torch.Size([24, 768]) torch.Size([24, 1])
torch.Size([50061, 2560]) torch.Size([50061, 768]) torch.Size([50061, 1])
torch.Size([5422, 2560]) torch.Size([5422, 768]) torch.Size([5422, 1])
torch.Size([13336, 2560]) torch.Size([13336, 768]) torch.Size([13336, 1])
3129


In [ ]:
initial_epoch = 0
best_epoch = -1
best_accuracy = 0.5
for epoch in range(initial_epoch, 500):
    torch.cuda.empty_cache()
    model.train()
    with tqdm(train_loader, desc='Processing', unit="batch") as tepoch:
        for ESP_train_df_enzy,ESP_train_df_smiles, y_train in tepoch:
            model.train()
            tepoch.set_description(f"Epoch {epoch}")
            ESP_train_df_enzy = ESP_train_df_enzy.to(device)
            ESP_train_df_smiles = ESP_train_df_smiles.to(device)
            y_train = y_train.squeeze(1).to(device)
            refined_enzy_embed, refined_smiles_embed = model(ESP_train_df_enzy,ESP_train_df_smiles)
            cosine_sim = torch.nn.functional.cosine_similarity(refined_enzy_embed, refined_smiles_embed, dim=1)
            loss = loss_fn(cosine_sim, y_train)
            loss.backward()
            optimizer.step()
            optimizer.zero_grad(set_to_none=True) #
            tepoch.set_postfix(train_loss=loss)
            # tepoch.set_postfix(val_loss=loss_sum_val, val_accuracy=100. * acc_val, balanced_val_accuracy=100. * bacc_val)
        loss_sum_val,acc_val, bacc_val = run_validation(model,val_loader,loss_fn, device)
        print('Epoch: %d / %d, ############## the best accuracy in val  %.4f at Epoch: %d  ##############'  % (epoch, 500,100 * best_accuracy,best_epoch))
        # print('Performance in Train: Loss: (%.4f); Accuracy (%.2f)' % (loss_sum, 100 * acc))
        print('Performance in Val: Loss: (%.4f); Accuracy (%.2f)' % (loss_sum_val, 100 * acc_val))
        # checkpoint(model, f"epoch-{epoch}.pth")
        if acc_val > best_accuracy: # compare the performance updates at the val set
            best_accuracy = acc_val
            best_epoch = epoch
            torch.save(model, "best_model.pt")

Epoch 0: 100%|██████████| 3129/3129 [00:30<00:00, 101.86batch/s, train_loss=tensor(0.2029, device='cuda:0', grad_fn=<MseLossBackward0>)]


loss_sum=  0.148264340787115 ACC=  0.800811508668388 bacc=  0.6824826509541646 precision=  0.6983050847457627 specificity=  0.9330994738160862 sensitivity=  0.43186582809224316 recall=  0.43186582809224316 MCC=  0.43526749179422664 AUC=  0.8184721528400467 f1=  0.533678756476684
Epoch: 0 / 500, ############## the best accuracy in val  50.0000 at Epoch: -1  ##############
Performance in Val: Loss: (0.1483); Accuracy (80.08)


Epoch 1: 100%|██████████| 3129/3129 [00:29<00:00, 107.48batch/s, train_loss=tensor(0.1887, device='cuda:0', grad_fn=<MseLossBackward0>)]


loss_sum=  0.13453260236653256 ACC=  0.8273699741792696 bacc=  0.7175566758259894 precision=  0.7771556550951848 specificity=  0.9501378100726635 sensitivity=  0.48497554157931516 recall=  0.48497554157931516 MCC=  0.5170543557041885 AUC=  0.8649845625753684 f1=  0.5972461273666093
Epoch: 1 / 500, ############## the best accuracy in val  80.0812 at Epoch: 0  ##############
Performance in Val: Loss: (0.1345); Accuracy (82.74)


Epoch 2: 100%|██████████| 3129/3129 [00:29<00:00, 107.86batch/s, train_loss=tensor(0.0982, device='cuda:0', grad_fn=<MseLossBackward0>)]


...

loss_sum=  0.07281350827663258 ACC=  0.932128365916636 bacc=  0.899658228218243 precision=  0.9041825095057034 specificity=  0.9684289651716362 sensitivity=  0.8308874912648497 recall=  0.8308874912648497 MCC=  0.8219666693507744 AUC=  0.9526619204881144 f1=  0.8659868900218499
Epoch: 497 / 500, ############## the best accuracy in val  93.6555 at Epoch: 482  ##############
Performance in Val: Loss: (0.0728); Accuracy (93.21)


Epoch 498: 100%|██████████| 3129/3129 [00:32<00:00, 97.54batch/s, train_loss=tensor(0.0296, device='cuda:0', grad_fn=<MseLossBackward0>)]


loss_sum=  0.07334898264974268 ACC=  0.9347104389524161 bacc=  0.9011880504720526 precision=  0.9145496535796767 specificity=  0.9721874216988223 sensitivity=  0.8301886792452831 recall=  0.8301886792452831 MCC=  0.8285665995654362 AUC=  0.9516451323654321 f1=  0.8703296703296703
Epoch: 498 / 500, ############## the best accuracy in val  93.6555 at Epoch: 482  ##############
Performance in Val: Loss: (0.0733); Accuracy (93.47)


Epoch 499: 100%|██████████| 3129/3129 [00:32<00:00, 96.60batch/s, train_loss=tensor(0.0604, device='cuda:0', grad_fn=<MseLossBackward0>)]


loss_sum=  0.07135207172768922 ACC=  0.9350793065289561 bacc=  0.899869745361725 precision=  0.9204988308651598 specificity=  0.9744424956151341 sensitivity=  0.8252969951083159 recall=  0.8252969951083159 MCC=  0.82936973105962 AUC=  0.9543598358360819 f1=  0.8703021370670597
Epoch: 499 / 500, ############## the best accuracy in val  93.6555 at Epoch: 482  ##############
Performance in Val: Loss: (0.0714); Accuracy (93.51)


In [ ]:
import torch
# Specify the file path where the entire model is saved
load_path = 'best_model.pt'
# Load the entire model
model_test = torch.load(load_path)
# model_test.to('cuda')
# rename the baseline model
torch.save(model_test, '5500_threshold_best_model_esm2_2560_botlle_neck128_batch_16_no_relu.pt')
run_validation(model_test,test_loader,loss_fn, device) # performance evaluation

loss_sum=  0.14964440478038765 ACC=  0.8426814637072585 bacc=  0.7323232288125971 precision=  0.8392344497607656 specificity=  0.9657841140529532 sensitivity=  0.4988623435722412 recall=  0.4988623435722412 MCC=  0.5631584759799391 AUC=  0.870054800400381 f1=  0.6257581163039599


(0.14964440478038765, 0.8426814637072585, 0.7323232288125971)

#### bottle neck 128
no batchnorm layer

In [ ]:
import os
os.chdir('/content/drive/MyDrive/EC_number_kroll/esm2_2560')

In [ ]:
import torch
import torch.nn as nn

class Contrastive_learning_layer(nn.Module):
    def __init__(self):
        super().__init__()
        self.enzy_refine_layer_1 = nn.Linear(2560, 2560) # W1 and b
        self.smiles_refine_layer_1 = nn.Linear(768, 768) # W1 and b
        self.enzy_refine_layer_2 = nn.Linear(2560, 128) # W1 and b
        self.smiles_refine_layer_2 = nn.Linear(768, 128) # W1 and b

        self.relu = nn.ReLU()
        # self.batch_norm_enzy = nn.BatchNorm1d(2560)
        # self.batch_norm_smiles = nn.BatchNorm1d(768)
        # self.batch_norm_shared = nn.BatchNorm1d(512)

    def forward(self, enzy_embed, smiles_embed):
        refined_enzy_embed = self.enzy_refine_layer_1(enzy_embed)
        refined_smiles_embed = self.smiles_refine_layer_1(smiles_embed)

        # refined_enzy_embed = self.batch_norm_enzy(refined_enzy_embed)
        # refined_smiles_embed = self.batch_norm_smiles(refined_smiles_embed)

        refined_enzy_embed = self.relu(refined_enzy_embed)
        refined_smiles_embed = self.relu(refined_smiles_embed)

        refined_enzy_embed = self.enzy_refine_layer_2(refined_enzy_embed)
        refined_smiles_embed = self.smiles_refine_layer_2(refined_smiles_embed)

        # refined_enzy_embed = self.batch_norm_shared(refined_enzy_embed)
        # refined_smiles_embed = self.batch_norm_shared(refined_smiles_embed)
        refined_enzy_embed = torch.nn.functional.normalize(refined_enzy_embed, dim=1)
        refined_smiles_embed = torch.nn.functional.normalize(refined_smiles_embed, dim=1)

        return refined_enzy_embed, refined_smiles_embed


In [ ]:
def get_ds():
    # Load the saved embeddings_results
    ESP_train_df_enzy = torch.load('ESP_train_df_enzy_esm2_2560.pt')
    ESP_val_df_enzy = torch.load('ESP_val_df_enzy_esm2_2560.pt')
    ESP_test_df_enzy = torch.load('ESP_test_df_enzy_esm2_2560.pt')
    print(ESP_train_df_enzy.shape, ESP_val_df_enzy.shape, ESP_test_df_enzy.shape)
    # Load the saved embeddings_results
    ESP_train_df_smiles = torch.load('ESP_train_df_smiles_esm2_2560.pt')
    ESP_val_df_smiles = torch.load('ESP_val_df_smiles_esm2_2560.pt')
    ESP_test_df_smiles = torch.load('ESP_test_df_smiles_esm2_2560.pt')
    print(ESP_train_df_smiles.shape, ESP_val_df_smiles.shape, ESP_test_df_smiles.shape)

    y_train = torch.load( 'ESP_train_df_label_esm2_2560.pt')
    y_val = torch.load('ESP_val_df_label_esm2_2560.pt')
    y_test = torch.load('ESP_test_df_label_esm2_2560.pt')
    print(y_train.shape,y_val.shape, y_test.shape)
    ESP_train_df_enzy_add = torch.load('ESP_train_df_enzy_>2800_<5500.pt')
    ESP_train_df_smiles_add = torch.load('ESP_train_df_smiles_>2800_<5500.pt')
    y_train_add = torch.load('ESP_train_df_label_>2800_<5500.pt')

    ESP_val_df_enzy_add = torch.load('ESP_val_df_enzy_>2800_<8000.pt')
    ESP_test_df_enzy_add = torch.load('ESP_test_df_enzy_>2800_<8000.pt')
    ESP_val_df_smiles_add = torch.load('ESP_val_df_smiles_>2800_<8000.pt')
    ESP_test_df_smiles_add = torch.load('ESP_test_df_smiles_>2800_<8000.pt')
    y_val_add = torch.load('ESP_val_df_label_>2800_<8000.pt')
    y_test_add = torch.load('ESP_test_df_label_>2800_<8000.pt')
    print(ESP_val_df_enzy_add.shape, ESP_val_df_smiles_add.shape, y_val_add.shape)
    print(ESP_test_df_enzy_add.shape, ESP_test_df_smiles_add.shape, y_test_add.shape)

    ESP_train_df_enzy = torch.cat([ESP_train_df_enzy, ESP_train_df_enzy_add], dim=0)
    ESP_train_df_smiles = torch.cat([ESP_train_df_smiles, ESP_train_df_smiles_add], dim=0)
    y_train = torch.cat([y_train, y_train_add], dim=0)
    print(ESP_train_df_enzy.shape, ESP_train_df_smiles.shape, y_train.shape)

    ESP_val_df_enzy = torch.cat([ESP_val_df_enzy, ESP_val_df_enzy_add], dim=0)
    ESP_val_df_smiles = torch.cat([ESP_val_df_smiles, ESP_val_df_smiles_add], dim=0)
    y_val = torch.cat([y_val, y_val_add], dim=0)
    print(ESP_val_df_enzy.shape, ESP_val_df_smiles.shape, y_val.shape)
    ESP_test_df_enzy = torch.cat([ESP_test_df_enzy, ESP_test_df_enzy_add], dim=0)
    ESP_test_df_smiles = torch.cat([ESP_test_df_smiles, ESP_test_df_smiles_add], dim=0)
    y_test = torch.cat([y_test, y_test_add], dim=0)
    print(ESP_test_df_enzy.shape, ESP_test_df_smiles.shape, y_test.shape)

    train_tensor_dataset = TensorDataset(ESP_train_df_enzy,ESP_train_df_smiles, y_train)
    val_tensor_dataset = TensorDataset(ESP_val_df_enzy,ESP_val_df_smiles, y_val)
    test_tensor_dataset = TensorDataset(ESP_test_df_enzy, ESP_test_df_smiles, y_test)

    # Create TensorDataset and DataLoaders
    batch_size = 16
    train_loader = DataLoader(train_tensor_dataset, batch_size=batch_size, shuffle=True)
    val_loader = DataLoader(val_tensor_dataset, batch_size=batch_size, shuffle=False)
    test_loader = DataLoader(test_tensor_dataset, batch_size=batch_size, shuffle=False)
    print(len(train_loader))
    return train_loader,  val_loader, test_loader

In [ ]:
# design the model, optimizer and loss function
model = Contrastive_learning_layer().to(device)
train_loader,  val_loader, test_loader = get_ds()
optimizer = torch.optim.Adam(model.parameters(),lr= 1e-03)
loss_fn = nn.MSELoss().to(device)

torch.Size([49881, 2560]) torch.Size([5399, 2560]) torch.Size([13312, 2560])
torch.Size([49881, 768]) torch.Size([5399, 768]) torch.Size([13312, 768])
torch.Size([49881, 1]) torch.Size([5399, 1]) torch.Size([13312, 1])
torch.Size([23, 2560]) torch.Size([23, 768]) torch.Size([23, 1])
torch.Size([24, 2560]) torch.Size([24, 768]) torch.Size([24, 1])
torch.Size([50061, 2560]) torch.Size([50061, 768]) torch.Size([50061, 1])
torch.Size([5422, 2560]) torch.Size([5422, 768]) torch.Size([5422, 1])
torch.Size([13336, 2560]) torch.Size([13336, 768]) torch.Size([13336, 1])
3129


In [ ]:
initial_epoch = 0
best_epoch = -1
best_accuracy = 0.5
for epoch in range(initial_epoch, 500):
    torch.cuda.empty_cache()
    model.train()
    with tqdm(train_loader, desc='Processing', unit="batch") as tepoch:
        for ESP_train_df_enzy,ESP_train_df_smiles, y_train in tepoch:
            model.train()
            tepoch.set_description(f"Epoch {epoch}")
            ESP_train_df_enzy = ESP_train_df_enzy.to(device)
            ESP_train_df_smiles = ESP_train_df_smiles.to(device)
            y_train = y_train.squeeze(1).to(device)
            refined_enzy_embed, refined_smiles_embed = model(ESP_train_df_enzy,ESP_train_df_smiles)
            cosine_sim = torch.nn.functional.cosine_similarity(refined_enzy_embed, refined_smiles_embed, dim=1)
            loss = loss_fn(cosine_sim, y_train)
            loss.backward()
            optimizer.step()
            optimizer.zero_grad(set_to_none=True) #
            tepoch.set_postfix(train_loss=loss)
            # tepoch.set_postfix(val_loss=loss_sum_val, val_accuracy=100. * acc_val, balanced_val_accuracy=100. * bacc_val)
        loss_sum_val,acc_val, bacc_val = run_validation(model,val_loader,loss_fn, device)
        print('Epoch: %d / %d, ############## the best accuracy in val  %.4f at Epoch: %d  ##############'  % (epoch, 500,100 * best_accuracy,best_epoch))
        # print('Performance in Train: Loss: (%.4f); Accuracy (%.2f)' % (loss_sum, 100 * acc))
        print('Performance in Val: Loss: (%.4f); Accuracy (%.2f)' % (loss_sum_val, 100 * acc_val))
        # checkpoint(model, f"epoch-{epoch}.pth")
        if acc_val > best_accuracy: # compare the performance updates at the val set
            best_accuracy = acc_val
            best_epoch = epoch
            torch.save(model, "best_model.pt")

Epoch 0: 100%|██████████| 3129/3129 [00:30<00:00, 103.73batch/s, train_loss=tensor(0.2104, device='cuda:0', grad_fn=<MseLossBackward0>)]


loss_sum=  0.1701558397363069 ACC=  0.7655846551088159 bacc=  0.5646458024615483 precision=  0.8361344537815126 specificity=  0.990228013029316 sensitivity=  0.13906359189378056 recall=  0.13906359189378056 MCC=  0.2781698346038008 AUC=  0.695500673160313 f1=  0.23846614739364888
Epoch: 0 / 500, ############## the best accuracy in val  50.0000 at Epoch: -1  ##############
Performance in Val: Loss: (0.1702); Accuracy (76.56)


Epoch 1: 100%|██████████| 3129/3129 [00:28<00:00, 110.49batch/s, train_loss=tensor(0.1227, device='cuda:0', grad_fn=<MseLossBackward0>)]


loss_sum=  0.14493871216489151 ACC=  0.7939874585023976 bacc=  0.6339188926307112 precision=  0.7962264150943397 specificity=  0.9729391130042596 sensitivity=  0.2948986722571628 recall=  0.2948986722571628 MCC=  0.3975130282409981 AUC=  0.8039222072164115 f1=  0.43039265680775124
Epoch: 1 / 500, ############## the best accuracy in val  76.5585 at Epoch: 0  ##############
Performance in Val: Loss: (0.1449); Accuracy (79.40)


Epoch 2: 100%|██████████| 3129/3129 [00:28<00:00, 109.40batch/s, train_loss=tensor(0.0804, device='cuda:0', grad_fn=<MseLossBackward0>)]


...

loss_sum=  0.06072522494062825 ACC=  0.932312799704906 bacc=  0.9006800066046579 precision=  0.9024205748865356 specificity=  0.967677273866199 sensitivity=  0.8336827393431167 recall=  0.8336827393431167 MCC=  0.8225848237798582 AUC=  0.9511576623923745 f1=  0.8666908826734472
Epoch: 497 / 500, ############## the best accuracy in val  93.5817 at Epoch: 186  ##############
Performance in Val: Loss: (0.0607); Accuracy (93.23)


Epoch 498: 100%|██████████| 3129/3129 [00:29<00:00, 104.95batch/s, train_loss=tensor(0.0087, device='cuda:0', grad_fn=<MseLossBackward0>)]


loss_sum=  0.060543228428694765 ACC=  0.9317594983400959 bacc=  0.8985111679475886 precision=  0.9052711993888465 specificity=  0.9689300927085943 sensitivity=  0.8280922431865828 recall=  0.8280922431865828 MCC=  0.8208843860052275 AUC=  0.9531929896074693 f1=  0.864963503649635
Epoch: 498 / 500, ############## the best accuracy in val  93.5817 at Epoch: 186  ##############
Performance in Val: Loss: (0.0605); Accuracy (93.18)


Epoch 499: 100%|██████████| 3129/3129 [00:29<00:00, 105.02batch/s, train_loss=tensor(0.0122, device='cuda:0', grad_fn=<MseLossBackward0>)]


loss_sum=  0.061459984288569455 ACC=  0.9312061969752858 bacc=  0.8990318187970452 precision=  0.9007575757575758 specificity=  0.9671761463292408 sensitivity=  0.8308874912648497 recall=  0.8308874912648497 MCC=  0.8196216290869873 AUC=  0.9512439852001034 f1=  0.8644129407488186
Epoch: 499 / 500, ############## the best accuracy in val  93.5817 at Epoch: 186  ##############
Performance in Val: Loss: (0.0615); Accuracy (93.12)


In [ ]:
import torch
# Specify the file path where the entire model is saved
load_path = 'best_model.pt'
# Load the entire model
model_test = torch.load(load_path)
# model_test.to('cuda')
# rename the baseline model
torch.save(model_test, '5500_threshold_best_model_esm2_2560_no_BatchNorm_batch_16_bottle128.pt')
run_validation(model_test,test_loader,loss_fn, device) # performance evaluation

loss_sum=  0.06833975325211937 ACC=  0.9201409718056389 bacc=  0.8841528050992958 precision=  0.8792943361188487 specificity=  0.960285132382892 sensitivity=  0.8080204778156996 recall=  0.8080204778156996 MCC=  0.7900917802039261 AUC=  0.9447500254872113 f1=  0.8421520675855935


(0.06833975325211937, 0.9201409718056389, 0.8841528050992958)

#### bottle neck 128
no normalization layer


In [ ]:
import os
os.chdir('/content/drive/MyDrive/EC_number_kroll/esm2_2560')

In [ ]:
import torch
import torch.nn as nn

class Contrastive_learning_layer(nn.Module):
    def __init__(self):
        super().__init__()
        self.enzy_refine_layer_1 = nn.Linear(2560, 2560) # W1 and b
        self.smiles_refine_layer_1 = nn.Linear(768, 768) # W1 and b
        self.enzy_refine_layer_2 = nn.Linear(2560, 128) # W1 and b
        self.smiles_refine_layer_2 = nn.Linear(768, 128) # W1 and b

        self.relu = nn.ReLU()
        self.batch_norm_enzy = nn.BatchNorm1d(2560)
        self.batch_norm_smiles = nn.BatchNorm1d(768)
        self.batch_norm_shared = nn.BatchNorm1d(128)

    def forward(self, enzy_embed, smiles_embed):
        refined_enzy_embed = self.enzy_refine_layer_1(enzy_embed)
        refined_smiles_embed = self.smiles_refine_layer_1(smiles_embed)

        refined_enzy_embed = self.batch_norm_enzy(refined_enzy_embed)
        refined_smiles_embed = self.batch_norm_smiles(refined_smiles_embed)

        refined_enzy_embed = self.relu(refined_enzy_embed)
        refined_smiles_embed = self.relu(refined_smiles_embed)

        refined_enzy_embed = self.enzy_refine_layer_2(refined_enzy_embed)
        refined_smiles_embed = self.smiles_refine_layer_2(refined_smiles_embed)

        refined_enzy_embed = self.batch_norm_shared(refined_enzy_embed)
        refined_smiles_embed = self.batch_norm_shared(refined_smiles_embed)
        # refined_enzy_embed = torch.nn.functional.normalize(refined_enzy_embed, dim=1)
        # refined_smiles_embed = torch.nn.functional.normalize(refined_smiles_embed, dim=1)

        return refined_enzy_embed, refined_smiles_embed


In [ ]:
def get_ds():
    # Load the saved embeddings_results
    ESP_train_df_enzy = torch.load('ESP_train_df_enzy_esm2_2560.pt')
    ESP_val_df_enzy = torch.load('ESP_val_df_enzy_esm2_2560.pt')
    ESP_test_df_enzy = torch.load('ESP_test_df_enzy_esm2_2560.pt')
    print(ESP_train_df_enzy.shape, ESP_val_df_enzy.shape, ESP_test_df_enzy.shape)
    # Load the saved embeddings_results
    ESP_train_df_smiles = torch.load('ESP_train_df_smiles_esm2_2560.pt')
    ESP_val_df_smiles = torch.load('ESP_val_df_smiles_esm2_2560.pt')
    ESP_test_df_smiles = torch.load('ESP_test_df_smiles_esm2_2560.pt')
    print(ESP_train_df_smiles.shape, ESP_val_df_smiles.shape, ESP_test_df_smiles.shape)

    y_train = torch.load( 'ESP_train_df_label_esm2_2560.pt')
    y_val = torch.load('ESP_val_df_label_esm2_2560.pt')
    y_test = torch.load('ESP_test_df_label_esm2_2560.pt')
    print(y_train.shape,y_val.shape, y_test.shape)
    ESP_train_df_enzy_add = torch.load('ESP_train_df_enzy_>2800_<5500.pt')
    ESP_train_df_smiles_add = torch.load('ESP_train_df_smiles_>2800_<5500.pt')
    y_train_add = torch.load('ESP_train_df_label_>2800_<5500.pt')

    ESP_val_df_enzy_add = torch.load('ESP_val_df_enzy_>2800_<8000.pt')
    ESP_test_df_enzy_add = torch.load('ESP_test_df_enzy_>2800_<8000.pt')
    ESP_val_df_smiles_add = torch.load('ESP_val_df_smiles_>2800_<8000.pt')
    ESP_test_df_smiles_add = torch.load('ESP_test_df_smiles_>2800_<8000.pt')
    y_val_add = torch.load('ESP_val_df_label_>2800_<8000.pt')
    y_test_add = torch.load('ESP_test_df_label_>2800_<8000.pt')
    print(ESP_val_df_enzy_add.shape, ESP_val_df_smiles_add.shape, y_val_add.shape)
    print(ESP_test_df_enzy_add.shape, ESP_test_df_smiles_add.shape, y_test_add.shape)

    ESP_train_df_enzy = torch.cat([ESP_train_df_enzy, ESP_train_df_enzy_add], dim=0)
    ESP_train_df_smiles = torch.cat([ESP_train_df_smiles, ESP_train_df_smiles_add], dim=0)
    y_train = torch.cat([y_train, y_train_add], dim=0)
    print(ESP_train_df_enzy.shape, ESP_train_df_smiles.shape, y_train.shape)

    ESP_val_df_enzy = torch.cat([ESP_val_df_enzy, ESP_val_df_enzy_add], dim=0)
    ESP_val_df_smiles = torch.cat([ESP_val_df_smiles, ESP_val_df_smiles_add], dim=0)
    y_val = torch.cat([y_val, y_val_add], dim=0)
    print(ESP_val_df_enzy.shape, ESP_val_df_smiles.shape, y_val.shape)
    ESP_test_df_enzy = torch.cat([ESP_test_df_enzy, ESP_test_df_enzy_add], dim=0)
    ESP_test_df_smiles = torch.cat([ESP_test_df_smiles, ESP_test_df_smiles_add], dim=0)
    y_test = torch.cat([y_test, y_test_add], dim=0)
    print(ESP_test_df_enzy.shape, ESP_test_df_smiles.shape, y_test.shape)

    train_tensor_dataset = TensorDataset(ESP_train_df_enzy,ESP_train_df_smiles, y_train)
    val_tensor_dataset = TensorDataset(ESP_val_df_enzy,ESP_val_df_smiles, y_val)
    test_tensor_dataset = TensorDataset(ESP_test_df_enzy, ESP_test_df_smiles, y_test)

    # Create TensorDataset and DataLoaders
    batch_size = 16
    train_loader = DataLoader(train_tensor_dataset, batch_size=batch_size, shuffle=True)
    val_loader = DataLoader(val_tensor_dataset, batch_size=batch_size, shuffle=False)
    test_loader = DataLoader(test_tensor_dataset, batch_size=batch_size, shuffle=False)
    print(len(train_loader))
    return train_loader,  val_loader, test_loader

In [ ]:
# design the model, optimizer and loss function
model = Contrastive_learning_layer().to(device)
train_loader,  val_loader, test_loader = get_ds()
optimizer = torch.optim.Adam(model.parameters(),lr= 1e-03)
loss_fn = nn.MSELoss().to(device)

torch.Size([49881, 2560]) torch.Size([5399, 2560]) torch.Size([13312, 2560])
torch.Size([49881, 768]) torch.Size([5399, 768]) torch.Size([13312, 768])
torch.Size([49881, 1]) torch.Size([5399, 1]) torch.Size([13312, 1])
torch.Size([23, 2560]) torch.Size([23, 768]) torch.Size([23, 1])
torch.Size([24, 2560]) torch.Size([24, 768]) torch.Size([24, 1])
torch.Size([50061, 2560]) torch.Size([50061, 768]) torch.Size([50061, 1])
torch.Size([5422, 2560]) torch.Size([5422, 768]) torch.Size([5422, 1])
torch.Size([13336, 2560]) torch.Size([13336, 768]) torch.Size([13336, 1])
3129


In [ ]:
initial_epoch = 0
best_epoch = -1
best_accuracy = 0.5
for epoch in range(initial_epoch, 500):
    torch.cuda.empty_cache()
    model.train()
    with tqdm(train_loader, desc='Processing', unit="batch") as tepoch:
        for ESP_train_df_enzy,ESP_train_df_smiles, y_train in tepoch:
            model.train()
            tepoch.set_description(f"Epoch {epoch}")
            ESP_train_df_enzy = ESP_train_df_enzy.to(device)
            ESP_train_df_smiles = ESP_train_df_smiles.to(device)
            y_train = y_train.squeeze(1).to(device)
            refined_enzy_embed, refined_smiles_embed = model(ESP_train_df_enzy,ESP_train_df_smiles)
            cosine_sim = torch.nn.functional.cosine_similarity(refined_enzy_embed, refined_smiles_embed, dim=1)
            loss = loss_fn(cosine_sim, y_train)
            loss.backward()
            optimizer.step()
            optimizer.zero_grad(set_to_none=True) #
            tepoch.set_postfix(train_loss=loss)
            # tepoch.set_postfix(val_loss=loss_sum_val, val_accuracy=100. * acc_val, balanced_val_accuracy=100. * bacc_val)
        loss_sum_val,acc_val, bacc_val = run_validation(model,val_loader,loss_fn, device)
        print('Epoch: %d / %d, ############## the best accuracy in val  %.4f at Epoch: %d  ##############'  % (epoch, 500,100 * best_accuracy,best_epoch))
        # print('Performance in Train: Loss: (%.4f); Accuracy (%.2f)' % (loss_sum, 100 * acc))
        print('Performance in Val: Loss: (%.4f); Accuracy (%.2f)' % (loss_sum_val, 100 * acc_val))
        # checkpoint(model, f"epoch-{epoch}.pth")
        if acc_val > best_accuracy: # compare the performance updates at the val set
            best_accuracy = acc_val
            best_epoch = epoch
            torch.save(model, "best_model.pt")

Epoch 0: 100%|██████████| 3129/3129 [00:28<00:00, 110.66batch/s, train_loss=tensor(0.1425, device='cuda:0', grad_fn=<MseLossBackward0>)]


loss_sum=  0.1640680214956095 ACC=  0.7914053854666175 bacc=  0.6583874689399857 precision=  0.6928020565552699 specificity=  0.9401152593335004 sensitivity=  0.376659678546471 recall=  0.376659678546471 MCC=  0.3982681632417829 AUC=  0.7821586164957807 f1=  0.4880036215482119
Epoch: 0 / 500, ############## the best accuracy in val  50.0000 at Epoch: -1  ##############
Performance in Val: Loss: (0.1641); Accuracy (79.14)


Epoch 1: 100%|██████████| 3129/3129 [00:27<00:00, 112.85batch/s, train_loss=tensor(0.1462, device='cuda:0', grad_fn=<MseLossBackward0>)]


loss_sum=  0.13149593292480022 ACC=  0.8240501659904095 bacc=  0.7173187190395721 precision=  0.7567276641550054 specificity=  0.9433725883237284 sensitivity=  0.4912648497554158 recall=  0.4912648497554158 MCC=  0.5084072635219508 AUC=  0.8556954930564421 f1=  0.5957627118644068
Epoch: 1 / 500, ############## the best accuracy in val  79.1405 at Epoch: 0  ##############
Performance in Val: Loss: (0.1315); Accuracy (82.41)


Epoch 2: 100%|██████████| 3129/3129 [00:27<00:00, 113.39batch/s, train_loss=tensor(0.0927, device='cuda:0', grad_fn=<MseLossBackward0>)]


...

loss_sum=  0.056830352139288345 ACC=  0.9391368498708963 bacc=  0.9136080289666424 precision=  0.9050772626931567 specificity=  0.967677273866199 sensitivity=  0.859538784067086 recall=  0.859538784067086 MCC=  0.8412914933535726 AUC=  0.9617673132822786 f1=  0.8817204301075269
Epoch: 497 / 500, ############## the best accuracy in val  94.3379 at Epoch: 254  ##############
Performance in Val: Loss: (0.0568); Accuracy (93.91)


Epoch 498: 100%|██████████| 3129/3129 [00:28<00:00, 110.71batch/s, train_loss=tensor(0.0348, device='cuda:0', grad_fn=<MseLossBackward0>)]


loss_sum=  0.05685072522995043 ACC=  0.9391368498708963 bacc=  0.9133839048410985 precision=  0.9056742815033162 specificity=  0.967927837634678 sensitivity=  0.8588399720475192 recall=  0.8588399720475192 MCC=  0.8412479926654792 AUC=  0.9622469038915478 f1=  0.8816355810616929
Epoch: 498 / 500, ############## the best accuracy in val  94.3379 at Epoch: 254  ##############
Performance in Val: Loss: (0.0569); Accuracy (93.91)


Epoch 499: 100%|██████████| 3129/3129 [00:27<00:00, 111.77batch/s, train_loss=tensor(0.0112, device='cuda:0', grad_fn=<MseLossBackward0>)]


loss_sum=  0.05656663994620771 ACC=  0.9402434526005164 bacc=  0.9134632237699043 precision=  0.9115241635687732 specificity=  0.9701829115509897 sensitivity=  0.856743535988819 recall=  0.856743535988819 MCC=  0.84390986768899 AUC=  0.9620599003242972 f1=  0.88328530259366
Epoch: 499 / 500, ############## the best accuracy in val  94.3379 at Epoch: 254  ##############
Performance in Val: Loss: (0.0566); Accuracy (94.02)


In [ ]:
import torch
# Specify the file path where the entire model is saved
load_path = 'best_model.pt'
# Load the entire model
model_test = torch.load(load_path)
# model_test.to('cuda')
# rename the baseline model
torch.save(model_test, '5500_threshold_best_model_esm2_2560_no_normalize_batch_16.pt')
run_validation(model_test,test_loader,loss_fn, device) # performance evaluation

loss_sum=  0.06138385461260312 ACC=  0.9342381523695261 bacc=  0.9043148110818394 precision=  0.9029007633587787 specificity=  0.9676171079429735 sensitivity=  0.8410125142207053 recall=  0.8410125142207053 MCC=  0.8277584007901977 AUC=  0.9591175719260685 f1=  0.8708584891768517


(0.06138385461260312, 0.9342381523695261, 0.9043148110818394)

#### bottle neck 128

only one dense layer and no ReLU

In [4]:
import os
os.chdir('/content/drive/MyDrive/EC_number_kroll/esm2_2560')

In [5]:
import torch
import torch.nn as nn

class Contrastive_learning_layer(nn.Module):
    def __init__(self):
        super().__init__()
        # self.enzy_refine_layer_1 = nn.Linear(2560, 2560) # W1 and b
        # self.smiles_refine_layer_1 = nn.Linear(768, 768) # W1 and b
        self.enzy_refine_layer_2 = nn.Linear(2560, 128) # W1 and b
        self.smiles_refine_layer_2 = nn.Linear(768, 128) # W1 and b

        self.relu = nn.ReLU()
        # self.batch_norm_enzy = nn.BatchNorm1d(2560)
        # self.batch_norm_smiles = nn.BatchNorm1d(768)
        self.batch_norm_shared = nn.BatchNorm1d(128)

    def forward(self, enzy_embed, smiles_embed):
        # refined_enzy_embed = self.enzy_refine_layer_1(enzy_embed)
        # refined_smiles_embed = self.smiles_refine_layer_1(smiles_embed)

        # refined_enzy_embed = self.batch_norm_enzy(refined_enzy_embed)
        # refined_smiles_embed = self.batch_norm_smiles(refined_smiles_embed)


        refined_enzy_embed = self.enzy_refine_layer_2(enzy_embed)
        refined_smiles_embed = self.smiles_refine_layer_2(smiles_embed)

        # refined_enzy_embed = self.relu(refined_enzy_embed)
        # refined_smiles_embed = self.relu(refined_smiles_embed)

        refined_enzy_embed = self.batch_norm_shared(refined_enzy_embed)
        refined_smiles_embed = self.batch_norm_shared(refined_smiles_embed)
        refined_enzy_embed = torch.nn.functional.normalize(refined_enzy_embed, dim=1)
        refined_smiles_embed = torch.nn.functional.normalize(refined_smiles_embed, dim=1)

        return refined_enzy_embed, refined_smiles_embed


In [6]:
def get_ds():
    # Load the saved embeddings_results
    ESP_train_df_enzy = torch.load('ESP_train_df_enzy_esm2_2560.pt')
    ESP_val_df_enzy = torch.load('ESP_val_df_enzy_esm2_2560.pt')
    ESP_test_df_enzy = torch.load('ESP_test_df_enzy_esm2_2560.pt')
    print(ESP_train_df_enzy.shape, ESP_val_df_enzy.shape, ESP_test_df_enzy.shape)
    # Load the saved embeddings_results
    ESP_train_df_smiles = torch.load('ESP_train_df_smiles_esm2_2560.pt')
    ESP_val_df_smiles = torch.load('ESP_val_df_smiles_esm2_2560.pt')
    ESP_test_df_smiles = torch.load('ESP_test_df_smiles_esm2_2560.pt')
    print(ESP_train_df_smiles.shape, ESP_val_df_smiles.shape, ESP_test_df_smiles.shape)

    y_train = torch.load( 'ESP_train_df_label_esm2_2560.pt')
    y_val = torch.load('ESP_val_df_label_esm2_2560.pt')
    y_test = torch.load('ESP_test_df_label_esm2_2560.pt')
    print(y_train.shape,y_val.shape, y_test.shape)
    ESP_train_df_enzy_add = torch.load('ESP_train_df_enzy_>2800_<5500.pt')
    ESP_train_df_smiles_add = torch.load('ESP_train_df_smiles_>2800_<5500.pt')
    y_train_add = torch.load('ESP_train_df_label_>2800_<5500.pt')

    ESP_val_df_enzy_add = torch.load('ESP_val_df_enzy_>2800_<8000.pt')
    ESP_test_df_enzy_add = torch.load('ESP_test_df_enzy_>2800_<8000.pt')
    ESP_val_df_smiles_add = torch.load('ESP_val_df_smiles_>2800_<8000.pt')
    ESP_test_df_smiles_add = torch.load('ESP_test_df_smiles_>2800_<8000.pt')
    y_val_add = torch.load('ESP_val_df_label_>2800_<8000.pt')
    y_test_add = torch.load('ESP_test_df_label_>2800_<8000.pt')
    print(ESP_val_df_enzy_add.shape, ESP_val_df_smiles_add.shape, y_val_add.shape)
    print(ESP_test_df_enzy_add.shape, ESP_test_df_smiles_add.shape, y_test_add.shape)

    ESP_train_df_enzy = torch.cat([ESP_train_df_enzy, ESP_train_df_enzy_add], dim=0)
    ESP_train_df_smiles = torch.cat([ESP_train_df_smiles, ESP_train_df_smiles_add], dim=0)
    y_train = torch.cat([y_train, y_train_add], dim=0)
    print(ESP_train_df_enzy.shape, ESP_train_df_smiles.shape, y_train.shape)

    ESP_val_df_enzy = torch.cat([ESP_val_df_enzy, ESP_val_df_enzy_add], dim=0)
    ESP_val_df_smiles = torch.cat([ESP_val_df_smiles, ESP_val_df_smiles_add], dim=0)
    y_val = torch.cat([y_val, y_val_add], dim=0)
    print(ESP_val_df_enzy.shape, ESP_val_df_smiles.shape, y_val.shape)
    ESP_test_df_enzy = torch.cat([ESP_test_df_enzy, ESP_test_df_enzy_add], dim=0)
    ESP_test_df_smiles = torch.cat([ESP_test_df_smiles, ESP_test_df_smiles_add], dim=0)
    y_test = torch.cat([y_test, y_test_add], dim=0)
    print(ESP_test_df_enzy.shape, ESP_test_df_smiles.shape, y_test.shape)

    train_tensor_dataset = TensorDataset(ESP_train_df_enzy,ESP_train_df_smiles, y_train)
    val_tensor_dataset = TensorDataset(ESP_val_df_enzy,ESP_val_df_smiles, y_val)
    test_tensor_dataset = TensorDataset(ESP_test_df_enzy, ESP_test_df_smiles, y_test)

    # Create TensorDataset and DataLoaders
    batch_size = 16
    train_loader = DataLoader(train_tensor_dataset, batch_size=batch_size, shuffle=True)
    val_loader = DataLoader(val_tensor_dataset, batch_size=batch_size, shuffle=False)
    test_loader = DataLoader(test_tensor_dataset, batch_size=batch_size, shuffle=False)
    print(len(train_loader))
    return train_loader,  val_loader, test_loader

In [7]:
# design the model, optimizer and loss function
model = Contrastive_learning_layer().to(device)
train_loader,  val_loader, test_loader = get_ds()
optimizer = torch.optim.Adam(model.parameters(),lr= 1e-03)
loss_fn = nn.MSELoss().to(device)

torch.Size([49881, 2560]) torch.Size([5399, 2560]) torch.Size([13312, 2560])
torch.Size([49881, 768]) torch.Size([5399, 768]) torch.Size([13312, 768])
torch.Size([49881, 1]) torch.Size([5399, 1]) torch.Size([13312, 1])
torch.Size([23, 2560]) torch.Size([23, 768]) torch.Size([23, 1])
torch.Size([24, 2560]) torch.Size([24, 768]) torch.Size([24, 1])
torch.Size([50061, 2560]) torch.Size([50061, 768]) torch.Size([50061, 1])
torch.Size([5422, 2560]) torch.Size([5422, 768]) torch.Size([5422, 1])
torch.Size([13336, 2560]) torch.Size([13336, 768]) torch.Size([13336, 1])
3129


In [8]:
initial_epoch = 0
best_epoch = -1
best_accuracy = 0.5
for epoch in range(initial_epoch, 500):
    torch.cuda.empty_cache()
    model.train()
    with tqdm(train_loader, desc='Processing', unit="batch") as tepoch:
        for ESP_train_df_enzy,ESP_train_df_smiles, y_train in tepoch:
            model.train()
            tepoch.set_description(f"Epoch {epoch}")
            ESP_train_df_enzy = ESP_train_df_enzy.to(device)
            ESP_train_df_smiles = ESP_train_df_smiles.to(device)
            y_train = y_train.squeeze(1).to(device)
            refined_enzy_embed, refined_smiles_embed = model(ESP_train_df_enzy,ESP_train_df_smiles)
            cosine_sim = torch.nn.functional.cosine_similarity(refined_enzy_embed, refined_smiles_embed, dim=1)
            loss = loss_fn(cosine_sim, y_train)
            loss.backward()
            optimizer.step()
            optimizer.zero_grad(set_to_none=True) #
            tepoch.set_postfix(train_loss=loss)
            # tepoch.set_postfix(val_loss=loss_sum_val, val_accuracy=100. * acc_val, balanced_val_accuracy=100. * bacc_val)
        loss_sum_val,acc_val, bacc_val = run_validation(model,val_loader,loss_fn, device)
        print('Epoch: %d / %d, ############## the best accuracy in val  %.4f at Epoch: %d  ##############'  % (epoch, 500,100 * best_accuracy,best_epoch))
        # print('Performance in Train: Loss: (%.4f); Accuracy (%.2f)' % (loss_sum, 100 * acc))
        print('Performance in Val: Loss: (%.4f); Accuracy (%.2f)' % (loss_sum_val, 100 * acc_val))
        # checkpoint(model, f"epoch-{epoch}.pth")
        if acc_val > best_accuracy: # compare the performance updates at the val set
            best_accuracy = acc_val
            best_epoch = epoch
            torch.save(model, "best_model.pt")

Epoch 0: 100%|██████████| 3129/3129 [00:23<00:00, 132.21batch/s, train_loss=tensor(0.1694, device='cuda:0', grad_fn=<MseLossBackward0>)]


loss_sum=  0.419729775427717 ACC=  0.7369974179269643 bacc=  0.5125049880750207 precision=  0.5247524752475248 specificity=  0.9879729391130042 sensitivity=  0.037037037037037035 recall=  0.037037037037037035 MCC=  0.08152984975511599 AUC=  0.6603672904146138 f1=  0.06919060052219321
Epoch: 0 / 500, ############## the best accuracy in val  50.0000 at Epoch: -1  ##############
Performance in Val: Loss: (0.4197); Accuracy (73.70)


Epoch 1: 100%|██████████| 3129/3129 [00:22<00:00, 140.22batch/s, train_loss=tensor(0.0940, device='cuda:0', grad_fn=<MseLossBackward0>)]


loss_sum=  0.43733468227593947 ACC=  0.7405016599040944 bacc=  0.5148853438755718 precision=  0.6463414634146342 specificity=  0.9927336507141067 sensitivity=  0.037037037037037035 recall=  0.037037037037037035 MCC=  0.10751572646964103 AUC=  0.6870942674826886 f1=  0.07005948446794448
Epoch: 1 / 500, ############## the best accuracy in val  73.6997 at Epoch: 0  ##############
Performance in Val: Loss: (0.4373); Accuracy (74.05)


Epoch 2: 100%|██████████| 3129/3129 [00:22<00:00, 140.51batch/s, train_loss=tensor(0.0696, device='cuda:0', grad_fn=<MseLossBackward0>)]


...

Epoch 498: 100%|██████████| 3129/3129 [00:21<00:00, 143.93batch/s, train_loss=tensor(0.0184, device='cuda:0', grad_fn=<MseLossBackward0>)]
<ipython-input-3-c7858174dfc2>:33: RuntimeWarning: invalid value encountered in scalar divide
  precision = tp/(tp+fp)
<ipython-input-3-c7858174dfc2>:35: RuntimeWarning: invalid value encountered in scalar divide
  MCC = (tp*tn-fp*fn)/np.sqrt((tp+fp)*(tp+fn)*(tn+fp)*(tn+fn))


loss_sum=  1.322749258142657 ACC=  0.7360752489856142 bacc=  0.5 precision=  nan specificity=  1.0 sensitivity=  0.0 recall=  0.0 MCC=  nan AUC=  0.7970303903559389 f1=  nan
Epoch: 498 / 500, ############## the best accuracy in val  74.0502 at Epoch: 1  ##############
Performance in Val: Loss: (1.3227); Accuracy (73.61)


Epoch 499: 100%|██████████| 3129/3129 [00:22<00:00, 140.03batch/s, train_loss=tensor(0.0378, device='cuda:0', grad_fn=<MseLossBackward0>)]


loss_sum=  1.3219282999854525 ACC=  0.7360752489856142 bacc=  0.5 precision=  nan specificity=  1.0 sensitivity=  0.0 recall=  0.0 MCC=  nan AUC=  0.7979648829012729 f1=  nan
Epoch: 499 / 500, ############## the best accuracy in val  74.0502 at Epoch: 1  ##############
Performance in Val: Loss: (1.3219); Accuracy (73.61)


<ipython-input-3-c7858174dfc2>:33: RuntimeWarning: invalid value encountered in scalar divide
  precision = tp/(tp+fp)
<ipython-input-3-c7858174dfc2>:35: RuntimeWarning: invalid value encountered in scalar divide
  MCC = (tp*tn-fp*fn)/np.sqrt((tp+fp)*(tp+fn)*(tn+fp)*(tn+fn))


In [9]:
import torch
# Specify the file path where the entire model is saved
load_path = 'best_model.pt'
# Load the entire model
model_test = torch.load(load_path)
# model_test.to('cuda')
# rename the baseline model
torch.save(model_test, '5500_threshold_best_model_esm2_2560_botlle_neck128_batch_16_no_relu_additional_test.pt')
run_validation(model_test,test_loader,loss_fn, device) # performance evaluation

loss_sum=  0.44959126041679504 ACC=  0.7389772045590882 bacc=  0.5102720991498856 precision=  0.6158940397350994 specificity=  0.9940936863543788 sensitivity=  0.026450511945392493 recall=  0.026450511945392493 MCC=  0.08555410152277441 AUC=  0.6866899845686522 f1=  0.050722661576220344


(0.44959126041679504, 0.7389772045590882, 0.5102720991498856)

#### bottle neck 128

without both bachnorm and L2 normalization


In [ ]:
import os
os.chdir('/content/drive/MyDrive/EC_number_kroll/esm2_2560')

In [ ]:
import torch
import torch.nn as nn

class Contrastive_learning_layer(nn.Module):
    def __init__(self):
        super().__init__()
        self.enzy_refine_layer_1 = nn.Linear(2560, 2560) # W1 and b
        self.smiles_refine_layer_1 = nn.Linear(768, 768) # W1 and b
        self.enzy_refine_layer_2 = nn.Linear(2560, 128) # W1 and b
        self.smiles_refine_layer_2 = nn.Linear(768, 128) # W1 and b

        self.relu = nn.ReLU()
        # self.batch_norm_enzy = nn.BatchNorm1d(2560)
        # self.batch_norm_smiles = nn.BatchNorm1d(768)
        # self.batch_norm_shared = nn.BatchNorm1d(128)

    def forward(self, enzy_embed, smiles_embed):
        refined_enzy_embed = self.enzy_refine_layer_1(enzy_embed)
        refined_smiles_embed = self.smiles_refine_layer_1(smiles_embed)

        # refined_enzy_embed = self.batch_norm_enzy(refined_enzy_embed)
        # refined_smiles_embed = self.batch_norm_smiles(refined_smiles_embed)

        refined_enzy_embed = self.relu(refined_enzy_embed)
        refined_smiles_embed = self.relu(refined_smiles_embed)

        refined_enzy_embed = self.enzy_refine_layer_2(refined_enzy_embed)
        refined_smiles_embed = self.smiles_refine_layer_2(refined_smiles_embed)

        # refined_enzy_embed = self.batch_norm_shared(refined_enzy_embed)
        # refined_smiles_embed = self.batch_norm_shared(refined_smiles_embed)
        # refined_enzy_embed = torch.nn.functional.normalize(refined_enzy_embed, dim=1)
        # refined_smiles_embed = torch.nn.functional.normalize(refined_smiles_embed, dim=1)

        return refined_enzy_embed, refined_smiles_embed


In [ ]:
def get_ds():
    # Load the saved embeddings_results
    ESP_train_df_enzy = torch.load('ESP_train_df_enzy_esm2_2560.pt')
    ESP_val_df_enzy = torch.load('ESP_val_df_enzy_esm2_2560.pt')
    ESP_test_df_enzy = torch.load('ESP_test_df_enzy_esm2_2560.pt')
    print(ESP_train_df_enzy.shape, ESP_val_df_enzy.shape, ESP_test_df_enzy.shape)
    # Load the saved embeddings_results
    ESP_train_df_smiles = torch.load('ESP_train_df_smiles_esm2_2560.pt')
    ESP_val_df_smiles = torch.load('ESP_val_df_smiles_esm2_2560.pt')
    ESP_test_df_smiles = torch.load('ESP_test_df_smiles_esm2_2560.pt')
    print(ESP_train_df_smiles.shape, ESP_val_df_smiles.shape, ESP_test_df_smiles.shape)

    y_train = torch.load( 'ESP_train_df_label_esm2_2560.pt')
    y_val = torch.load('ESP_val_df_label_esm2_2560.pt')
    y_test = torch.load('ESP_test_df_label_esm2_2560.pt')
    print(y_train.shape,y_val.shape, y_test.shape)
    ESP_train_df_enzy_add = torch.load('ESP_train_df_enzy_>2800_<5500.pt')
    ESP_train_df_smiles_add = torch.load('ESP_train_df_smiles_>2800_<5500.pt')
    y_train_add = torch.load('ESP_train_df_label_>2800_<5500.pt')

    ESP_val_df_enzy_add = torch.load('ESP_val_df_enzy_>2800_<8000.pt')
    ESP_test_df_enzy_add = torch.load('ESP_test_df_enzy_>2800_<8000.pt')
    ESP_val_df_smiles_add = torch.load('ESP_val_df_smiles_>2800_<8000.pt')
    ESP_test_df_smiles_add = torch.load('ESP_test_df_smiles_>2800_<8000.pt')
    y_val_add = torch.load('ESP_val_df_label_>2800_<8000.pt')
    y_test_add = torch.load('ESP_test_df_label_>2800_<8000.pt')
    print(ESP_val_df_enzy_add.shape, ESP_val_df_smiles_add.shape, y_val_add.shape)
    print(ESP_test_df_enzy_add.shape, ESP_test_df_smiles_add.shape, y_test_add.shape)

    ESP_train_df_enzy = torch.cat([ESP_train_df_enzy, ESP_train_df_enzy_add], dim=0)
    ESP_train_df_smiles = torch.cat([ESP_train_df_smiles, ESP_train_df_smiles_add], dim=0)
    y_train = torch.cat([y_train, y_train_add], dim=0)
    print(ESP_train_df_enzy.shape, ESP_train_df_smiles.shape, y_train.shape)

    ESP_val_df_enzy = torch.cat([ESP_val_df_enzy, ESP_val_df_enzy_add], dim=0)
    ESP_val_df_smiles = torch.cat([ESP_val_df_smiles, ESP_val_df_smiles_add], dim=0)
    y_val = torch.cat([y_val, y_val_add], dim=0)
    print(ESP_val_df_enzy.shape, ESP_val_df_smiles.shape, y_val.shape)
    ESP_test_df_enzy = torch.cat([ESP_test_df_enzy, ESP_test_df_enzy_add], dim=0)
    ESP_test_df_smiles = torch.cat([ESP_test_df_smiles, ESP_test_df_smiles_add], dim=0)
    y_test = torch.cat([y_test, y_test_add], dim=0)
    print(ESP_test_df_enzy.shape, ESP_test_df_smiles.shape, y_test.shape)

    train_tensor_dataset = TensorDataset(ESP_train_df_enzy,ESP_train_df_smiles, y_train)
    val_tensor_dataset = TensorDataset(ESP_val_df_enzy,ESP_val_df_smiles, y_val)
    test_tensor_dataset = TensorDataset(ESP_test_df_enzy, ESP_test_df_smiles, y_test)

    # Create TensorDataset and DataLoaders
    batch_size = 16
    train_loader = DataLoader(train_tensor_dataset, batch_size=batch_size, shuffle=True)
    val_loader = DataLoader(val_tensor_dataset, batch_size=batch_size, shuffle=False)
    test_loader = DataLoader(test_tensor_dataset, batch_size=batch_size, shuffle=False)
    print(len(train_loader))
    return train_loader,  val_loader, test_loader

In [ ]:
# design the model, optimizer and loss function
model = Contrastive_learning_layer().to(device)
train_loader,  val_loader, test_loader = get_ds()
optimizer = torch.optim.Adam(model.parameters(),lr= 1e-03)
loss_fn = nn.MSELoss().to(device)

torch.Size([49881, 2560]) torch.Size([5399, 2560]) torch.Size([13312, 2560])
torch.Size([49881, 768]) torch.Size([5399, 768]) torch.Size([13312, 768])
torch.Size([49881, 1]) torch.Size([5399, 1]) torch.Size([13312, 1])
torch.Size([23, 2560]) torch.Size([23, 768]) torch.Size([23, 1])
torch.Size([24, 2560]) torch.Size([24, 768]) torch.Size([24, 1])
torch.Size([50061, 2560]) torch.Size([50061, 768]) torch.Size([50061, 1])
torch.Size([5422, 2560]) torch.Size([5422, 768]) torch.Size([5422, 1])
torch.Size([13336, 2560]) torch.Size([13336, 768]) torch.Size([13336, 1])
3129


In [ ]:
initial_epoch = 0
best_epoch = -1
best_accuracy = 0.5
for epoch in range(initial_epoch, 300):
    torch.cuda.empty_cache()
    model.train()
    with tqdm(train_loader, desc='Processing', unit="batch") as tepoch:
        for ESP_train_df_enzy,ESP_train_df_smiles, y_train in tepoch:
            model.train()
            tepoch.set_description(f"Epoch {epoch}")
            ESP_train_df_enzy = ESP_train_df_enzy.to(device)
            ESP_train_df_smiles = ESP_train_df_smiles.to(device)
            y_train = y_train.squeeze(1).to(device)
            refined_enzy_embed, refined_smiles_embed = model(ESP_train_df_enzy,ESP_train_df_smiles)
            cosine_sim = torch.nn.functional.cosine_similarity(refined_enzy_embed, refined_smiles_embed, dim=1)
            loss = loss_fn(cosine_sim, y_train)
            loss.backward()
            optimizer.step()
            optimizer.zero_grad(set_to_none=True) #
            tepoch.set_postfix(train_loss=loss)
            # tepoch.set_postfix(val_loss=loss_sum_val, val_accuracy=100. * acc_val, balanced_val_accuracy=100. * bacc_val)
        loss_sum_val,acc_val, bacc_val = run_validation(model,val_loader,loss_fn, device)
        print('Epoch: %d / %d, ############## the best accuracy in val  %.4f at Epoch: %d  ##############'  % (epoch, 500,100 * best_accuracy,best_epoch))
        # print('Performance in Train: Loss: (%.4f); Accuracy (%.2f)' % (loss_sum, 100 * acc))
        print('Performance in Val: Loss: (%.4f); Accuracy (%.2f)' % (loss_sum_val, 100 * acc_val))
        # checkpoint(model, f"epoch-{epoch}.pth")
        if acc_val > best_accuracy: # compare the performance updates at the val set
            best_accuracy = acc_val
            best_epoch = epoch
            torch.save(model, "best_model.pt")

Epoch 0: 100%|██████████| 3129/3129 [00:30<00:00, 103.16batch/s, train_loss=tensor(0.1548, device='cuda:0', grad_fn=<MseLossBackward0>)]


loss_sum=  0.16663547947035778 ACC=  0.7689044632976761 bacc=  0.5787794550316829 precision=  0.7730061349693251 specificity=  0.9814582811325482 sensitivity=  0.1761006289308176 recall=  0.1761006289308176 MCC=  0.2921326773257354 AUC=  0.7200126735189116 f1=  0.28685258964143423
Epoch: 0 / 500, ############## the best accuracy in val  50.0000 at Epoch: -1  ##############
Performance in Val: Loss: (0.1666); Accuracy (76.89)


Epoch 1: 100%|██████████| 3129/3129 [00:29<00:00, 104.75batch/s, train_loss=tensor(0.1098, device='cuda:0', grad_fn=<MseLossBackward0>)]


loss_sum=  0.14530774680100886 ACC=  0.7969383991147179 bacc=  0.6332339132720178 precision=  0.8367346938775511 specificity=  0.9799548985216737 sensitivity=  0.286512928022362 recall=  0.286512928022362 MCC=  0.40963389632970776 AUC=  0.8007807048738768 f1=  0.426861009890682
Epoch: 1 / 500, ############## the best accuracy in val  76.8904 at Epoch: 0  ##############
Performance in Val: Loss: (0.1453); Accuracy (79.69)


Epoch 2: 100%|██████████| 3129/3129 [00:30<00:00, 103.62batch/s, train_loss=tensor(0.0894, device='cuda:0', grad_fn=<MseLossBackward0>)]


...

loss_sum=  0.05982565871253747 ACC=  0.9363703430468462 bacc=  0.9050050769367345 precision=  0.91324200913242 specificity=  0.9714357303933852 sensitivity=  0.8385744234800838 recall=  0.8385744234800838 MCC=  0.833178862903504 AUC=  0.9520594118037422 f1=  0.8743169398907104
Epoch: 297 / 500, ############## the best accuracy in val  94.1166 at Epoch: 92  ##############
Performance in Val: Loss: (0.0598); Accuracy (93.64)


Epoch 298: 100%|██████████| 3129/3129 [00:28<00:00, 108.08batch/s, train_loss=tensor(0.0093, device='cuda:0', grad_fn=<MseLossBackward0>)]


loss_sum=  0.05940730333504072 ACC=  0.9354481741054961 bacc=  0.9039304192644491 precision=  0.9110266159695818 specificity=  0.9706840390879479 sensitivity=  0.8371767994409504 recall=  0.8371767994409504 MCC=  0.8307531734113457 AUC=  0.953291569203314 f1=  0.8725418790968682
Epoch: 298 / 500, ############## the best accuracy in val  94.1166 at Epoch: 92  ##############
Performance in Val: Loss: (0.0594); Accuracy (93.54)


Epoch 299: 100%|██████████| 3129/3129 [00:28<00:00, 108.29batch/s, train_loss=tensor(0.0104, device='cuda:0', grad_fn=<MseLossBackward0>)]


loss_sum=  0.058483714995367295 ACC=  0.9358170416820362 bacc=  0.9064222242883665 precision=  0.9062265566391597 specificity=  0.9686795289401152 sensitivity=  0.8441649196366178 recall=  0.8441649196366178 MCC=  0.8320405545716765 AUC=  0.9551633558455512 f1=  0.874095513748191
Epoch: 299 / 500, ############## the best accuracy in val  94.1166 at Epoch: 92  ##############
Performance in Val: Loss: (0.0585); Accuracy (93.58)


In [ ]:
import torch
# Specify the file path where the entire model is saved
load_path = 'best_model.pt'
# Load the entire model
model_test = torch.load(load_path)
# model_test.to('cuda')
# rename the baseline model
torch.save(model_test, '5500_threshold_best_model_esm2_2560_botlle_neck128_batch_16_no_normaliztion_no_batchnorm.pt')
run_validation(model_test,test_loader,loss_fn, device) # performance evaluation

loss_sum=  0.06914040504649618 ACC=  0.9196910617876425 bacc=  0.8831169816654271 precision=  0.8795405153678981 specificity=  0.9604887983706721 sensitivity=  0.805745164960182 recall=  0.805745164960182 MCC=  0.7887934021765556 AUC=  0.9446772421215555 f1=  0.8410271634258573


(0.06914040504649618, 0.9196910617876425, 0.8831169816654271)

#### bottle neck 128

change loss function


In [ ]:
def run_validation(model, val_loader,loss_fn, device):
    model.eval()
    loss_sum = 0
    num_batch = len(val_loader)
    total_y_true=[]
    total_y_pred=[]
    total_y_prob=[]
    for ESP_val_df_enzy,ESP_val_df_smiles, y_val in val_loader:

        ESP_val_df_enzy = ESP_val_df_enzy.to(device)
        ESP_val_df_smiles = ESP_val_df_smiles.to(device)
        y_val = y_val.squeeze(1).to(device)

        refined_enzy_embed, refined_smiles_embed = model(ESP_val_df_enzy,ESP_val_df_smiles)
        cos_sim = torch.nn.functional.cosine_similarity(refined_enzy_embed, refined_smiles_embed, dim=1)
        score = torch.nn.functional.sigmoid(cos_sim)
        loss = loss_fn(score, y_val).detach().cpu().numpy()
        loss_sum = loss_sum + loss # count all the loss in the training process
        y_pred = (score > 0.5).float().cpu().numpy() # if score > 0.5, assign label 1 otherwise 0, transfer to cpu as numpy
        total_y_true.append(y_val.cpu().numpy())
        total_y_pred.append(y_pred)
        total_y_prob.append(cos_sim.detach().cpu().numpy())

    loss_sum = loss_sum/num_batch # get the overall average loss (Notice: this method is not 100% accurate)

    arrange_y_true = np.concatenate(total_y_true, axis=0)
    arrange_y_pred = np.concatenate(total_y_pred, axis=0)
    arrange_y_prob = np.concatenate(total_y_prob, axis=0)
    tn,fp,fn,tp = confusion_matrix(arrange_y_true, arrange_y_pred).ravel()
    acc = (tp+tn)/(tp+tn+fp+fn)
    specificity = tn/(tn+fp)
    sensitivity = tp/(tp+fn)
    recall = tp/(tp+fn)
    precision = tp/(tp+fp)
    bacc = (sensitivity + specificity)/2
    MCC = (tp*tn-fp*fn)/np.sqrt((tp+fp)*(tp+fn)*(tn+fp)*(tn+fn))
    AUC = roc_auc_score(arrange_y_true, arrange_y_prob)
    f1 = 2*precision*recall/(precision+recall)
    print("loss_sum= ",loss_sum, "ACC= ",acc, "bacc= ",bacc, "precision= ",precision,"specificity= ",specificity, "sensitivity= ",sensitivity, "recall= ",recall, "MCC= ",MCC, "AUC= ",AUC, "f1= ",f1)
    return loss_sum, acc, bacc   # , precision, sensitivity, recall, MCC, AUC, f1


In [ ]:
import os
os.chdir('/content/drive/MyDrive/EC_number_kroll/esm2_2560')

In [ ]:
import torch
import torch.nn as nn

class Contrastive_learning_layer(nn.Module):
    def __init__(self):
        super().__init__()
        self.enzy_refine_layer_1 = nn.Linear(2560, 2560) # W1 and b
        self.smiles_refine_layer_1 = nn.Linear(768, 768) # W1 and b
        self.enzy_refine_layer_2 = nn.Linear(2560, 128) # W1 and b
        self.smiles_refine_layer_2 = nn.Linear(768, 128) # W1 and b

        self.relu = nn.ReLU()
        self.batch_norm_enzy = nn.BatchNorm1d(2560)
        self.batch_norm_smiles = nn.BatchNorm1d(768)
        self.batch_norm_shared = nn.BatchNorm1d(128)

    def forward(self, enzy_embed, smiles_embed):
        refined_enzy_embed = self.enzy_refine_layer_1(enzy_embed)
        refined_smiles_embed = self.smiles_refine_layer_1(smiles_embed)

        refined_enzy_embed = self.batch_norm_enzy(refined_enzy_embed)
        refined_smiles_embed = self.batch_norm_smiles(refined_smiles_embed)

        refined_enzy_embed = self.relu(refined_enzy_embed)
        refined_smiles_embed = self.relu(refined_smiles_embed)

        refined_enzy_embed = self.enzy_refine_layer_2(refined_enzy_embed)
        refined_smiles_embed = self.smiles_refine_layer_2(refined_smiles_embed)

        refined_enzy_embed = self.batch_norm_shared(refined_enzy_embed)
        refined_smiles_embed = self.batch_norm_shared(refined_smiles_embed)
        refined_enzy_embed = torch.nn.functional.normalize(refined_enzy_embed, dim=1)
        refined_smiles_embed = torch.nn.functional.normalize(refined_smiles_embed, dim=1)

        return refined_enzy_embed, refined_smiles_embed


In [ ]:
def get_ds():
    # Load the saved embeddings_results
    ESP_train_df_enzy = torch.load('ESP_train_df_enzy_esm2_2560.pt')
    ESP_val_df_enzy = torch.load('ESP_val_df_enzy_esm2_2560.pt')
    ESP_test_df_enzy = torch.load('ESP_test_df_enzy_esm2_2560.pt')
    print(ESP_train_df_enzy.shape, ESP_val_df_enzy.shape, ESP_test_df_enzy.shape)
    # Load the saved embeddings_results
    ESP_train_df_smiles = torch.load('ESP_train_df_smiles_esm2_2560.pt')
    ESP_val_df_smiles = torch.load('ESP_val_df_smiles_esm2_2560.pt')
    ESP_test_df_smiles = torch.load('ESP_test_df_smiles_esm2_2560.pt')
    print(ESP_train_df_smiles.shape, ESP_val_df_smiles.shape, ESP_test_df_smiles.shape)

    y_train = torch.load( 'ESP_train_df_label_esm2_2560.pt')
    y_val = torch.load('ESP_val_df_label_esm2_2560.pt')
    y_test = torch.load('ESP_test_df_label_esm2_2560.pt')
    print(y_train.shape,y_val.shape, y_test.shape)
    ESP_train_df_enzy_add = torch.load('ESP_train_df_enzy_>2800_<5500.pt')
    ESP_train_df_smiles_add = torch.load('ESP_train_df_smiles_>2800_<5500.pt')
    y_train_add = torch.load('ESP_train_df_label_>2800_<5500.pt')

    ESP_val_df_enzy_add = torch.load('ESP_val_df_enzy_>2800_<8000.pt')
    ESP_test_df_enzy_add = torch.load('ESP_test_df_enzy_>2800_<8000.pt')
    ESP_val_df_smiles_add = torch.load('ESP_val_df_smiles_>2800_<8000.pt')
    ESP_test_df_smiles_add = torch.load('ESP_test_df_smiles_>2800_<8000.pt')
    y_val_add = torch.load('ESP_val_df_label_>2800_<8000.pt')
    y_test_add = torch.load('ESP_test_df_label_>2800_<8000.pt')
    print(ESP_val_df_enzy_add.shape, ESP_val_df_smiles_add.shape, y_val_add.shape)
    print(ESP_test_df_enzy_add.shape, ESP_test_df_smiles_add.shape, y_test_add.shape)

    ESP_train_df_enzy = torch.cat([ESP_train_df_enzy, ESP_train_df_enzy_add], dim=0)
    ESP_train_df_smiles = torch.cat([ESP_train_df_smiles, ESP_train_df_smiles_add], dim=0)
    y_train = torch.cat([y_train, y_train_add], dim=0)
    print(ESP_train_df_enzy.shape, ESP_train_df_smiles.shape, y_train.shape)

    ESP_val_df_enzy = torch.cat([ESP_val_df_enzy, ESP_val_df_enzy_add], dim=0)
    ESP_val_df_smiles = torch.cat([ESP_val_df_smiles, ESP_val_df_smiles_add], dim=0)
    y_val = torch.cat([y_val, y_val_add], dim=0)
    print(ESP_val_df_enzy.shape, ESP_val_df_smiles.shape, y_val.shape)
    ESP_test_df_enzy = torch.cat([ESP_test_df_enzy, ESP_test_df_enzy_add], dim=0)
    ESP_test_df_smiles = torch.cat([ESP_test_df_smiles, ESP_test_df_smiles_add], dim=0)
    y_test = torch.cat([y_test, y_test_add], dim=0)
    print(ESP_test_df_enzy.shape, ESP_test_df_smiles.shape, y_test.shape)

    train_tensor_dataset = TensorDataset(ESP_train_df_enzy,ESP_train_df_smiles, y_train)
    val_tensor_dataset = TensorDataset(ESP_val_df_enzy,ESP_val_df_smiles, y_val)
    test_tensor_dataset = TensorDataset(ESP_test_df_enzy, ESP_test_df_smiles, y_test)

    # Create TensorDataset and DataLoaders
    batch_size = 16
    train_loader = DataLoader(train_tensor_dataset, batch_size=batch_size, shuffle=True)
    val_loader = DataLoader(val_tensor_dataset, batch_size=batch_size, shuffle=False)
    test_loader = DataLoader(test_tensor_dataset, batch_size=batch_size, shuffle=False)
    print(len(train_loader))
    return train_loader,  val_loader, test_loader

In [ ]:
# design the model, optimizer and loss function
model = Contrastive_learning_layer().to(device)
train_loader,  val_loader, test_loader = get_ds()
optimizer = torch.optim.Adam(model.parameters(),lr= 1e-03)
loss_fn = nn.BCELoss().to(device)

torch.Size([49881, 2560]) torch.Size([5399, 2560]) torch.Size([13312, 2560])
torch.Size([49881, 768]) torch.Size([5399, 768]) torch.Size([13312, 768])
torch.Size([49881, 1]) torch.Size([5399, 1]) torch.Size([13312, 1])
torch.Size([23, 2560]) torch.Size([23, 768]) torch.Size([23, 1])
torch.Size([24, 2560]) torch.Size([24, 768]) torch.Size([24, 1])
torch.Size([50061, 2560]) torch.Size([50061, 768]) torch.Size([50061, 1])
torch.Size([5422, 2560]) torch.Size([5422, 768]) torch.Size([5422, 1])
torch.Size([13336, 2560]) torch.Size([13336, 768]) torch.Size([13336, 1])
3129


In [ ]:
initial_epoch = 0
best_epoch = -1
best_accuracy = 0.5
for epoch in range(initial_epoch, 500):
    torch.cuda.empty_cache()
    model.train()
    with tqdm(train_loader, desc='Processing', unit="batch") as tepoch:
        for ESP_train_df_enzy,ESP_train_df_smiles, y_train in tepoch:
            model.train()
            tepoch.set_description(f"Epoch {epoch}")
            ESP_train_df_enzy = ESP_train_df_enzy.to(device)
            ESP_train_df_smiles = ESP_train_df_smiles.to(device)
            y_train = y_train.squeeze(1).to(device)
            refined_enzy_embed, refined_smiles_embed = model(ESP_train_df_enzy,ESP_train_df_smiles)
            cosine_sim = torch.nn.functional.cosine_similarity(refined_enzy_embed, refined_smiles_embed, dim=1)
            score = torch.nn.functional.sigmoid(cosine_sim)
            loss = loss_fn(score, y_train)
            loss.backward()
            optimizer.step()
            optimizer.zero_grad(set_to_none=True) #
            tepoch.set_postfix(train_loss=loss)
            # tepoch.set_postfix(val_loss=loss_sum_val, val_accuracy=100. * acc_val, balanced_val_accuracy=100. * bacc_val)
        loss_sum_val,acc_val, bacc_val = run_validation(model,val_loader,loss_fn, device)
        print('Epoch: %d / %d, ############## the best accuracy in val  %.4f at Epoch: %d  ##############'  % (epoch, 500,100 * best_accuracy,best_epoch))
        # print('Performance in Train: Loss: (%.4f); Accuracy (%.2f)' % (loss_sum, 100 * acc))
        print('Performance in Val: Loss: (%.4f); Accuracy (%.2f)' % (loss_sum_val, 100 * acc_val))
        # checkpoint(model, f"epoch-{epoch}.pth")
        if acc_val > best_accuracy: # compare the performance updates at the val set
            best_accuracy = acc_val
            best_epoch = epoch
            torch.save(model, "best_model_loss_fn_CE.pt")

Epoch 0: 100%|██████████| 3129/3129 [00:33<00:00, 92.80batch/s, train_loss=tensor(0.6449, device='cuda:0', grad_fn=<BinaryCrossEntropyBackward0>)]


loss_sum=  0.6153455778384982 ACC=  0.683880486905201 bacc=  0.6046228052251038 precision=  0.40769732550554466 specificity=  0.7724880982209973 sensitivity=  0.43675751222921033 recall=  0.43675751222921033 MCC=  0.20479860208813475 AUC=  0.6444008978272392 f1=  0.421727395411606
Epoch: 0 / 500, ############## the best accuracy in val  50.0000 at Epoch: -1  ##############
Performance in Val: Loss: (0.6153); Accuracy (68.39)


Epoch 1: 100%|██████████| 3129/3129 [00:32<00:00, 95.31batch/s, train_loss=tensor(0.5389, device='cuda:0', grad_fn=<BinaryCrossEntropyBackward0>)]


loss_sum=  0.6007438345996328 ACC=  0.7078568793803025 bacc=  0.6430977386050829 precision=  0.4522173641474079 specificity=  0.7802555750438487 sensitivity=  0.5059399021663172 recall=  0.5059399021663172 MCC=  0.2765280952696203 AUC=  0.696367140531605 f1=  0.47757255936675463
Epoch: 1 / 500, ############## the best accuracy in val  68.3880 at Epoch: 0  ##############
Performance in Val: Loss: (0.6007); Accuracy (70.79)


Epoch 2: 100%|██████████| 3129/3129 [00:32<00:00, 95.68batch/s, train_loss=tensor(0.5191, device='cuda:0', grad_fn=<BinaryCrossEntropyBackward0>)]


...

loss_sum=  0.5762594041571153 ACC=  0.7401327923275544 bacc=  0.7788771241232675 precision=  0.5045045045045045 specificity=  0.6968178401403157 sensitivity=  0.8609364081062194 recall=  0.8609364081062194 MCC=  0.49410881947073104 AUC=  0.8651179864688562 f1=  0.6361993286857733
Epoch: 497 / 500, ############## the best accuracy in val  76.5031 at Epoch: 18  ##############
Performance in Val: Loss: (0.5763); Accuracy (74.01)


Epoch 498: 100%|██████████| 3129/3129 [00:32<00:00, 95.38batch/s, train_loss=tensor(0.5433, device='cuda:0', grad_fn=<BinaryCrossEntropyBackward0>)]


loss_sum=  0.5754905481957404 ACC=  0.7386573220213943 bacc=  0.7754095036683691 precision=  0.5028830313014827 specificity=  0.697569531445753 sensitivity=  0.8532494758909853 recall=  0.8532494758909853 MCC=  0.4882242644471646 AUC=  0.8636970745323029 f1=  0.6328064265353718
Epoch: 498 / 500, ############## the best accuracy in val  76.5031 at Epoch: 18  ##############
Performance in Val: Loss: (0.5755); Accuracy (73.87)


Epoch 499: 100%|██████████| 3129/3129 [00:33<00:00, 94.70batch/s, train_loss=tensor(0.5946, device='cuda:0', grad_fn=<BinaryCrossEntropyBackward0>)]


loss_sum=  0.574865555956652 ACC=  0.7344153448911841 bacc=  0.7754416339629295 precision=  0.4981832862333468 specificity=  0.6885492357805061 sensitivity=  0.8623340321453529 recall=  0.8623340321453529 MCC=  0.4874326423141299 AUC=  0.8677484682954537 f1=  0.6315250767656091
Epoch: 499 / 500, ############## the best accuracy in val  76.5031 at Epoch: 18  ##############
Performance in Val: Loss: (0.5749); Accuracy (73.44)


In [ ]:
import torch
# Specify the file path where the entire model is saved
load_path = 'best_model_loss_fn_CE.pt'
# Load the entire model
model_test = torch.load(load_path)
# model_test.to('cuda')
# rename the baseline model
torch.save(model_test, '5500_threshold_best_model_esm2_2560_botlle_neck128_batch_16_only_one_bottleneck_layer.pt')
run_validation(model_test,test_loader,loss_fn, device) # performance evaluation

loss_sum=  0.5757881739942862 ACC=  0.7446760647870426 bacc=  0.7470239626125782 precision=  0.5107204944948812 specificity=  0.7420570264765785 sensitivity=  0.7519908987485779 recall=  0.7519908987485779 MCC=  0.44667506351734065 AUC=  0.8217221563802598 f1=  0.6083055331876223


(0.5757881739942862, 0.7446760647870426, 0.7470239626125782)